# Run various tests on models

In [117]:
from game.game import Game
from game.data.generator import create_numbers
import torch
import os

In [255]:
# loads checkpoint and does one epoch, shows acc on validation set
def load(last_save, model_size, model_number, run_number, vocab, sender, receiver, embedding, length=0):
    epochs = last_save + 1
    save_name = "game/models/game{}_{}_{}_{}_{}_{}_{}".format(model_size, model_number, run_number, vocab, sender, receiver, embedding)
    if(length > 0):
        save_name = "{}_{}".format(save_name, length)
    if(length == 0):
        length = 1
    

    params = [
        '--batch_size=1',
        '--n_epochs={}'.format(epochs),
        '--vocab_size={}'.format(vocab),
        '--sender_hidden={}'.format(sender),
        '--receiver_hidden={}'.format(receiver),
        '--lr=0.001',
        '--max_len={}'.format(length),
        '--sender_entropy=0.5',
        '--sender_embedding={}'.format(embedding),
        '--receiver_embedding={}'.format(embedding),
        '--validation_freq=10',
        '--train_data=game/data/train10.txt',
        '--validation_data=game/data/validation10.txt',
        '--load_from_checkpoint={}_{}.tar'.format(save_name, last_save)
    ]
    game = Game(params)
    game.play()
    return game

In [119]:
def predict_and_print(model, inputs, labels):
    inputs_tensor = torch.FloatTensor(inputs)
    labels_tensor = torch.FloatTensor(labels)
    prediction = model.game.forward(inputs_tensor,labels_tensor)
    messages = prediction[1].message.tolist()
    outputs = prediction[1].receiver_output.tolist()
    for q in range(len(outputs)):
        print("{} {} {} {}".format(inputs[q], messages[q], outputs[q], labels[q]))
    unique_outputs = set([item[0] for item in outputs])
    number_unique = len(unique_outputs)
    message_strings = ["_".join([ str(m) for m in message]) for message in messages]
    acc = prediction[1].aux['acc'].mean().item()            
    print("Unique outputs: {}: {}".format(number_unique, unique_outputs))
    print("Accuracy: {}".format(acc))
    return acc, number_unique, message_strings


In [247]:
def calc_polysemy(inputs, labels, message_strings):
    message_inputs = {}
    for r in range(len(inputs)):
        input = ",".join([ str(i) for i in inputs[r]])
        message = message_strings[r]
        label = labels[r][0]
        label_dict = message_inputs.get(message, {})
        message_inputs[message] = label_dict
        input_list = label_dict.get(label, [])
        input_list.append(input)
        message_inputs[message][label] = input_list

    polysemous = 0
    polysemous_ = 0
    polysemous_input = 0
    polyssemous_messages = []
    for message, labels in message_inputs.items():
        #if (len(labels)> 2):
        #    polysemous_ += 1
        #    polysemous_input += 1
        #el
        if (len(labels)> 1):
            polysemous += 1
            polysemous_input += 1
            polyssemous_messages.append(message)
        else:
            for label, inputs in labels.items(): 
                if (len(inputs)> 1):
                    polysemous_input += 1
                    
    print(message_inputs)
    print(1/len(set(message_strings)))
    percent_emitted = 0
    for message in polyssemous_messages:
        _percent_emitted =  message_strings.count(message)/len(message_strings)
        percent_emitted += _percent_emitted
        print("Polysemous {}: frequency {}".format(message,_percent_emitted))
    
    print("Each message frequency")
    for message in set(message_strings):
        count = message_strings.count(message)
        _percent_emitted =  count/len(message_strings)
        print("{}\t{}\t{}".format(message,count, _percent_emitted))
              
    print("Polysemous messages, 2 or more inputs: {}, {}, {}".format(polysemous_input, polysemous_input/len(message_inputs), polysemous_input/len(message_strings)))
    print("Polysemous messages, 2 or more labels: {}, {}, {}".format(polysemous, polysemous/len(message_inputs), percent_emitted))
  #  print("Polysemous messages, 3 or more labels: {}, {}, {}".format(polysemous_, polysemous_/len(message_inputs), polysemous_/len(message_strings)))
    return [polysemous_input, polysemous_input/len(message_inputs), polysemous_input/len(message_strings),polysemous, polysemous/len(message_inputs), percent_emitted]

In [4]:
extra_tests = {}
def test_above_limit(game, start, end, number_of_samples):
    # creates more samples for model to predict
    inputs, labels = extra_tests.get((start, end, number_of_samples), (None, None))
    if(inputs is None or labels is None):
        inputs, labels = create_numbers(end, number_of_samples, False, False, start)
        extra_tests[(start, end, number_of_samples)] = (inputs, labels)
        print("Inputs: {}".format(inputs))
        print("Labels: {}".format(labels))
        
    print("Testing {} samples of numbers that sum up to [{} - {}]".format(number_of_samples, start, end))
    return predict_and_print(game, inputs, labels)

In [144]:
def test_all_set(game, n):
    inputs = []
    labels = []
    for i in range(n+1):
        for j in range(n+1):
            if i+j <= n:
                inputs.append([i, j])
                labels.append([i+j]) 
    print("Testing {} samples of numbers that sum up to {}".format(len(inputs), n))
    a, m, message_strings = predict_and_print(game, inputs, labels)
    polysemy = calc_polysemy(inputs, labels, message_strings)
    return a, m, polysemy

In [6]:
def test_validation_only(game):
    frame = game.trainer.validation_data.dataset.frame
    inputs = [f[0].tolist() for f in frame]
    labels = [f[1].tolist() for f in frame]
    return predict_and_print(game, inputs, labels)

In [7]:
def test_some_other_numbers(game):
    inputs = [[9.0, 0.2], [0., 0.3],[6.0, 4.0],[6.0, 4.0],[9.0, 1.0],[9.0, 1.0],[9.0, 1.0],[1.0, 1.0],[1.0, 1.0],[1.0, 1.0], [0.0, 1.0], [0.0, 0.0], [-1.0, 4.0], [5.0, -2.0], [-1.0, 0.0], [-2.0, -2.0], [-9.0, -1.0], [8.0, -3.0], [-10.0, -10.0]]
    labels = [[9.2],[.3],[10.],[10.],[10.],[10.],[10.],[2.0],[2.0],[2.0],[1.0],[0.0],[3.0],[3.0], [-1.0], [-4.0], [-10.0], [5.0], [-20.0]]
    return predict_and_print(game, inputs, labels)

In [245]:
def test_synonymy(game, n, repeat):
    limit = n+1
    accs_input = {}
    messages_input = {}
    accs_label = {}
    messages_label = {}
    messages_emitted = 0
    all_messages = []
    for i in range(limit):
        for j in range(limit):
            if(i+j <= n):
                inputs = []
                labels = []
                for p in range(repeat):
                    messages_emitted += 1
                    inputs.append([i, j])
                    labels.append([i+j]) 
                
                a, m, ms = predict_and_print(game, inputs, labels)
                all_messages.append(ms)
                
                input = (inputs[0][0],inputs[0][1])
                label = labels[0][0]
                accs_input[input] = a
                messages_input[input] = m
                
                l = messages_label.get(label, [])
                l.append(ms)
                messages_label[label] = l
                
                l = accs_label.get(label, [])
                l.append(a)
                accs_label[label] = l
    
    
    #print(messages_label)
    print(messages_input)
    messages_label_count = {}
    label_messages = {}
    for i in range(limit):
        messages = [message for message_set in messages_label[i] for message in message_set]
        messages_label[i] = set(messages)
        for m in set(messages):
            l = label_messages.get(m,[])
            l.append(i)
            label_messages[m] = l
        messages_label_count[i] = len(set(messages))
        accs_label[i] = sum(accs_label[i])/len(accs_label[i])
        
    #print(label_messages)
    #print(messages_label)
    messages_messages = {}
    messages_messages_count = {}
    for message, labels in label_messages.items():
        l = []
        for label in labels:
            l.append(messages_label[label]) 
            # should consider not include all labels here, but only the labels that are correct
        l = [message for messages in l for message in messages] #flatten list
        messages_messages[message] = set(l) # uniques
        messages_messages_count[message] = len(set(l)) 
    #print(messages_messages)
    messages_w_syns = 0
    print(messages_messages_count)
    for k, count in messages_messages_count.items():
        if count > 1:
            messages_w_syns +=1
    print("Messages with synonyms: {}".format(messages_w_syns))
    
    
    all_flatten = [message for messages in all_messages for message in messages]
    emitted = len(all_flatten)
    unique = len(set(all_flatten))
    print("Each message frequency")
    for message in set(all_flatten):
        count = all_flatten.count(message)
        print("{}\t{}".format(message,count))
    print("Total messages {}, Unique messages: {}".format(emitted, unique))
    print("Unique messages per labels: {}".format(messages_label_count))    
    print("Unique messages per input: {}".format(messages_input))
    print("Accuracies per input: {}".format(accs_input))
    return accs_label, messages_label, _

In [9]:
def test_various_ranges(game, start_numbers, end_numbers, n_samples):
    accs = []
    ns_symbols = []
    for i in range(len(start_numbers)):  
        acc, n_symbols, _ = test_above_limit(game, start_numbers[i], end_numbers[i], n_samples[i])
        accs.append(acc)
        ns_symbols.append(n_symbols)
    print("Accuracies: {}".format(accs))
    print("Number of messages: {}".format(ns_symbols))
    return accs, ns_symbols, _

In [10]:
def run_test(games, test):
    accs = []
    ns_symbols= []
    
    for i in range(len(games)):
        print("\n--------")
        print("Running test for game {}".format(i))
        acc, n_symbols, _ = test(games[i])
        accs.append(acc)
        ns_symbols.append(n_symbols)
        
    print("\n--------")
    print("All games:")
    for i in range(len(accs)):
        print("Game {},  Number of messages: {}, Accuracy: {}".format(i, ns_symbols[i], accs[i]))

In [161]:
def run_n_tests(games, n, test):
    all_accs = []
    all_ns_symbols= []
    all_pis = []
    for i in range(len(games)):
        print("\n--------")
        print("Running tests for game {}".format(i))
        accs = []
        ns_symbols= []
        pis = []
        for j in range(n):
            acc, n_symbols, polysemy = test(games[i])
            accs.append(acc)
            ns_symbols.append(n_symbols)
            pis.append(polysemy)
        all_accs.append(sum(accs)/len(accs))
        all_ns_symbols.append(sum(ns_symbols)/len(ns_symbols))
        p = [sum(list(i))/len(list(i)) for i in zip(*pis)]
        all_pis.append(p) 
        
    print("\n--------")
    print("All games:")
    for i in range(len(all_accs)):
        print("Game {},  Number of messages: {}, Accuracy: {}, Polysemy: {}".format(i, all_ns_symbols[i], all_accs[i], all_pis[i]))

In [168]:
games10 = [
   # load(1, 10, 14, 1, 128, 128, 128, 8), # 0 game10_14_1_128_128_128_8_1
    load(6000, 10, 14, 1, 16, 16, 16, 5),# 1 game10_14_1_16_16_16_5_6000.tar
    load(1500, 10, 14, 1, 32, 32, 32, 7), # 2 game10_14_1_32_32_32_7_1500.tar
   # load(1500, 10, 14, 1, 32, 64, 32, 7), # 3 game10_14_1_32_64_32_7_1500.tar
   # load(1500, 10, 14, 1, 64, 64, 64, 7), # 4 game10_14_1_64_64_64_7_1500.tar
   # load(1500, 10, 14, 1, 64, 128, 64, 8), # 5game10_14_1_64_128_64_8_1500.tar
    load(6000, 10, 14, 3, 64, 64,64, 7), # 8
    load(6000, 10, 14, 1, 128, 128, 128, 8), #6
   # load(3000, 10, 14, 3, 64, 64,64, 7), # 7
   # load(1500, 10, 15, 1, 64, 64, 64, 7, 2), #game10_15_1_64_64_64_7_2_1500.tar
  #  load(1500, 10, 15, 2, 16, 16,16, 5, 2),
  #  load(6000, 10, 15, 1, 64, 64, 64, 7, 2),
    load(6000, 10, 15, 2, 16, 16,16, 5, 2), # 12
]

Preparing dataset...
Samples in training set: 52
Samples in test set: 14

----------
Building model...
# Initializing model, trainer, and optimizer from game/models/game10_14_1_16_16_16_5_6000.tar
# loading trainer state from game/models/game10_14_1_16_16_16_5_6000.tar
SenderReceiverRnnReinforce(
  (sender): RnnSenderReinforce(
    (agent): LayerWrapper(
      (output): Linear(in_features=2, out_features=16, bias=True)
    )
    (hidden_to_output): Linear(in_features=16, out_features=16, bias=True)
    (embedding): Embedding(16, 5)
    (cells): ModuleList(
      (0): RNNCell(5, 16)
    )
  )
  (receiver): RnnReceiverDeterministic(
    (agent): LayerWrapper(
      (output): Linear(in_features=16, out_features=1, bias=True)
    )
    (encoder): RnnEncoder(
      (cell): RNN(5, 16, batch_first=True)
      (embedding): Embedding(16, 5)
    )
  )
  (mechanics): CommunicationRnnReinforce()
)
Number of parameters 1238

----------
Start of training... 2021-11-12 01:34:56.438631
{"loss": -0.081

In [256]:
games30 = [
     load(6000, 30, 1, 1, 64, 64,64, 7, 1), #game30_1_1_64_64_64_7_1_6000 game30_1_1_64_64_64_7_6000
]

Preparing dataset...
Samples in training set: 52
Samples in test set: 14

----------
Building model...
# Initializing model, trainer, and optimizer from game/models/game30_1_1_64_64_64_7_1_6000.tar
# loading trainer state from game/models/game30_1_1_64_64_64_7_1_6000.tar
SenderReceiverRnnReinforce(
  (sender): RnnSenderReinforce(
    (agent): LayerWrapper(
      (output): Linear(in_features=2, out_features=64, bias=True)
    )
    (hidden_to_output): Linear(in_features=64, out_features=64, bias=True)
    (embedding): Embedding(64, 7)
    (cells): ModuleList(
      (0): RNNCell(7, 64)
    )
  )
  (receiver): RnnReceiverDeterministic(
    (agent): LayerWrapper(
      (output): Linear(in_features=64, out_features=1, bias=True)
    )
    (encoder): RnnEncoder(
      (cell): RNN(7, 64, batch_first=True)
      (embedding): Embedding(64, 7)
    )
  )
  (mechanics): CommunicationRnnReinforce()
)
Number of parameters 14664

----------
Start of training... 2021-11-12 07:47:39.334071
{"loss": 0.8

# Test whole number range with frequency and polysemy count

In [248]:
run_test(games10, lambda x: test_all_set(x, 10))


--------
Running test for game 0
Testing 66 samples of numbers that sum up to 10
[0, 0] [0, 0] [0.8094069957733154] [0]
[0, 1] [0, 0] [0.8094069957733154] [1]
[0, 2] [2, 0] [2.613788604736328] [2]
[0, 3] [2, 0] [2.613788604736328] [3]
[0, 4] [15, 0] [4.509095191955566] [4]
[0, 5] [15, 0] [4.509095191955566] [5]
[0, 6] [13, 0] [5.983450889587402] [6]
[0, 7] [8, 0] [7.006291389465332] [7]
[0, 8] [5, 0] [7.999305248260498] [8]
[0, 9] [9, 0] [9.471212387084961] [9]
[0, 10] [4, 0] [9.500732421875] [10]
[1, 0] [12, 0] [0.6528407335281372] [1]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 2] [2, 0] [2.613788604736328] [3]
[1, 3] [15, 0] [4.509095191955566] [4]
[1, 4] [13, 0] [5.983450889587402] [5]
[1, 5] [13, 0] [5.983450889587402] [6]
[1, 6] [8, 0] [7.006291389465332] [7]
[1, 7] [5, 0] [7.999305248260498] [8]
[1, 8] [10, 0] [9.49882698059082] [9]
[1, 9] [7, 0] [9.501371383666992] [10]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 1] [2, 0] [2.613788604736328] [3]
[2, 2] [15, 0] [4.509095191955566]

In [190]:
run_n_tests(games10, 20, lambda x: test_all_set(x, 10))


--------
Running tests for game 0
Testing 66 samples of numbers that sum up to 10
[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 1] [12, 0] [0.6528407335281372] [1]
[0, 2] [2, 0] [2.613788604736328] [2]
[0, 3] [2, 0] [2.613788604736328] [3]
[0, 4] [15, 0] [4.509095191955566] [4]
[0, 5] [15, 0] [4.509095191955566] [5]
[0, 6] [13, 0] [5.983450889587402] [6]
[0, 7] [8, 0] [7.006291389465332] [7]
[0, 8] [1, 0] [8.004281044006348] [8]
[0, 9] [4, 0] [9.500732421875] [9]
[0, 10] [10, 0] [9.49882698059082] [10]
[1, 0] [0, 0] [0.8094069957733154] [1]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 2] [2, 0] [2.613788604736328] [3]
[1, 3] [15, 0] [4.509095191955566] [4]
[1, 4] [15, 0] [4.509095191955566] [5]
[1, 5] [13, 0] [5.983450889587402] [6]
[1, 6] [8, 0] [7.006291389465332] [7]
[1, 7] [6, 0] [7.994237422943115] [8]
[1, 8] [4, 0] [9.500732421875] [9]
[1, 9] [10, 0] [9.49882698059082] [10]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 1] [2, 0] [2.613788604736328] [3]
[2, 2] [15, 0] [4.509095191955566] 

[8, 2] [3, 0] [9.499813079833984] [10]
[9, 0] [9, 0] [9.471212387084961] [9]
[9, 1] [3, 0] [9.499813079833984] [10]
[10, 0] [14, 0] [9.49847412109375] [10]
Unique outputs: 16: {0.8094069957733154, 0.6528407335281372, 2.613788604736328, 4.509095191955566, 5.983450889587402, 7.006291389465332, 7.994237422943115, 9.49847412109375, 9.471212387084961, 8.004281044006348, 7.999305248260498, 9.500732421875, 9.499813079833984, 9.48766803741455, 9.501371383666992, 9.49882698059082}
Accuracy: 0.6363636255264282
0.0625
0_0: 0.045454545454545456
2_0: 0.09090909090909091
15_0: 0.13636363636363635
13_0: 0.13636363636363635
6_0: 0.045454545454545456
14_0: 0.06060606060606061
9_0: 0.07575757575757576
4_0: 0.030303030303030304
3_0: 0.07575757575757576
10_0: 0.030303030303030304
Polysemous messages, 2 or more inputs: 14, 0.875, 0.21212121212121213
Polysemous messages, 2 or more labels: 10, 0.625, 0.7272727272727273
Testing 66 samples of numbers that sum up to 10
[0, 0] [12, 0] [0.6528407335281372] [0]
[0

[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 1] [12, 0] [0.6528407335281372] [1]
[0, 2] [2, 0] [2.613788604736328] [2]
[0, 3] [2, 0] [2.613788604736328] [3]
[0, 4] [15, 0] [4.509095191955566] [4]
[0, 5] [15, 0] [4.509095191955566] [5]
[0, 6] [13, 0] [5.983450889587402] [6]
[0, 7] [8, 0] [7.006291389465332] [7]
[0, 8] [5, 0] [7.999305248260498] [8]
[0, 9] [4, 0] [9.500732421875] [9]
[0, 10] [11, 0] [9.48766803741455] [10]
[1, 0] [0, 0] [0.8094069957733154] [1]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 2] [2, 0] [2.613788604736328] [3]
[1, 3] [15, 0] [4.509095191955566] [4]
[1, 4] [15, 0] [4.509095191955566] [5]
[1, 5] [13, 0] [5.983450889587402] [6]
[1, 6] [8, 0] [7.006291389465332] [7]
[1, 7] [5, 0] [7.999305248260498] [8]
[1, 8] [7, 0] [9.501371383666992] [9]
[1, 9] [11, 0] [9.48766803741455] [10]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 1] [2, 0] [2.613788604736328] [3]
[2, 2] [15, 0] [4.509095191955566] [4]
[2, 3] [15, 0] [4.509095191955566] [5]
[2, 4] [13, 0] [5.983450889587402] [6

[0, 0] [25, 0] [0.5386849641799927] [0]
[0, 1] [25, 0] [0.5386849641799927] [1]
[0, 2] [1, 0] [2.5937345027923584] [2]
[0, 3] [1, 0] [2.5937345027923584] [3]
[0, 4] [26, 0] [4.038124084472656] [4]
[0, 5] [13, 0] [5.307830810546875] [5]
[0, 6] [31, 0] [5.3101911544799805] [6]
[0, 7] [27, 0] [6.567420482635498] [7]
[0, 8] [19, 0] [7.818550109863281] [8]
[0, 9] [4, 0] [8.15825080871582] [9]
[0, 10] [21, 0] [9.351724624633789] [10]
[1, 0] [25, 0] [0.5386849641799927] [1]
[1, 1] [1, 0] [2.5937345027923584] [2]
[1, 2] [1, 0] [2.5937345027923584] [3]
[1, 3] [26, 0] [4.038124084472656] [4]
[1, 4] [13, 0] [5.307830810546875] [5]
[1, 5] [0, 0] [6.379913330078125] [6]
[1, 6] [10, 0] [6.617605209350586] [7]
[1, 7] [22, 0] [7.335894584655762] [8]
[1, 8] [11, 0] [8.73343563079834] [9]
[1, 9] [11, 0] [8.73343563079834] [10]
[2, 0] [1, 0] [2.5937345027923584] [2]
[2, 1] [1, 0] [2.5937345027923584] [3]
[2, 2] [26, 0] [4.038124084472656] [4]
[2, 3] [31, 0] [5.3101911544799805] [5]
[2, 4] [28, 0] [5.7056

[0, 0] [16, 0] [0.8063359260559082] [0]
[0, 1] [16, 0] [0.8063359260559082] [1]
[0, 2] [37, 0] [2.1050236225128174] [2]
[0, 3] [40, 0] [3.1406655311584473] [3]
[0, 4] [24, 0] [4.220020294189453] [4]
[0, 5] [0, 0] [4.165658950805664] [5]
[0, 6] [5, 0] [6.077377796173096] [6]
[0, 7] [14, 0] [6.980797290802002] [7]
[0, 8] [61, 0] [8.16197681427002] [8]
[0, 9] [9, 0] [9.163700103759766] [9]
[0, 10] [36, 0] [10.099649429321289] [10]
[1, 0] [16, 0] [0.8063359260559082] [1]
[1, 1] [40, 0] [3.1406655311584473] [2]
[1, 2] [40, 0] [3.1406655311584473] [3]
[1, 3] [0, 0] [4.165658950805664] [4]
[1, 4] [27, 0] [5.184774875640869] [5]
[1, 5] [35, 0] [6.194769859313965] [6]
[1, 6] [52, 0] [7.187754154205322] [7]
[1, 7] [34, 0] [8.06334114074707] [8]
[1, 8] [15, 0] [9.204402923583984] [9]
[1, 9] [42, 0] [10.087390899658203] [10]
[2, 0] [37, 0] [2.1050236225128174] [2]
[2, 1] [40, 0] [3.1406655311584473] [3]
[2, 2] [33, 0] [4.220180988311768] [4]
[2, 3] [47, 0] [5.006893157958984] [5]
[2, 4] [56, 0] [6

...

Unique outputs: 26: {0.6698111295700073, 1.9773046970367432, 2.815936326980591, 3.8364601135253906, 4.881392955780029, 5.707600116729736, 6.823071479797363, 7.840209484100342, 8.565916061401367, 9.483417510986328, 2.819763660430908, 3.7732067108154297, 5.729968547821045, 8.602348327636719, 9.494512557983398, 8.50341510772705, 9.526863098144531, 3.8902103900909424, 9.506338119506836, 4.782124996185303, 5.753654956817627, 5.789170742034912, 6.754367351531982, 8.56619930267334, 9.4153470993042, 9.499252319335938}
Accuracy: 0.7575757503509521
0.038461538461538464
23_0: 0.045454545454545456
84_0: 0.06060606060606061
44_0: 0.09090909090909091
119_0: 0.09090909090909091
59_0: 0.045454545454545456
111_0: 0.045454545454545456
62_0: 0.045454545454545456
1_0: 0.10606060606060606
Polysemous messages, 2 or more inputs: 16, 0.6153846153846154, 0.24242424242424243
Polysemous messages, 2 or more labels: 8, 0.3076923076923077, 0.5303030303030303
Testing 66 samples of numbers that sum up to 10
[0, 0] [2

[0, 0] [23, 0] [0.6698111295700073] [0]
[0, 1] [23, 0] [0.6698111295700073] [1]
[0, 2] [67, 0] [1.9773046970367432] [2]
[0, 3] [14, 0] [2.819763660430908] [3]
[0, 4] [29, 0] [3.8902103900909424] [4]
[0, 5] [127, 0] [4.874148368835449] [5]
[0, 6] [43, 0] [5.789170742034912] [6]
[0, 7] [113, 0] [6.754367351531982] [7]
[0, 8] [125, 0] [8.602348327636719] [8]
[0, 9] [35, 0] [8.56619930267334] [9]
[0, 10] [62, 0] [9.494512557983398] [10]
[1, 0] [23, 0] [0.6698111295700073] [1]
[1, 1] [67, 0] [1.9773046970367432] [2]
[1, 2] [14, 0] [2.819763660430908] [3]
[1, 3] [84, 0] [3.8364601135253906] [4]
[1, 4] [116, 0] [4.782124996185303] [5]
[1, 5] [86, 0] [5.707600116729736] [6]
[1, 6] [113, 0] [6.754367351531982] [7]
[1, 7] [119, 0] [7.840209484100342] [8]
[1, 8] [59, 0] [8.565916061401367] [9]
[1, 9] [1, 0] [9.526863098144531] [10]
[2, 0] [67, 0] [1.9773046970367432] [2]
[2, 1] [14, 0] [2.819763660430908] [3]
[2, 2] [84, 0] [3.8364601135253906] [4]
[2, 3] [68, 0] [4.881392955780029] [5]
[2, 4] [4

[0, 0] [3, 3, 0] [-0.010573148727416992] [0]
[0, 1] [3, 4, 0] [0.997984766960144] [1]
[0, 2] [7, 3, 0] [1.9896314144134521] [2]
[0, 3] [7, 7, 0] [2.992901086807251] [3]
[0, 4] [10, 12, 0] [4.001784801483154] [4]
[0, 5] [9, 7, 0] [5.957056045532227] [5]
[0, 6] [2, 2, 0] [5.8631181716918945] [6]
[0, 7] [5, 9, 0] [6.992199897766113] [7]
[0, 8] [12, 13, 0] [8.016786575317383] [8]
[0, 9] [12, 1, 0] [9.012248992919922] [9]
[0, 10] [1, 11, 0] [9.991928100585938] [10]
[1, 0] [3, 7, 0] [0.9984374046325684] [1]
[1, 1] [4, 3, 0] [1.9769492149353027] [2]
[1, 2] [4, 0, 0] [2.9690911769866943] [3]
[1, 3] [7, 15, 0] [3.9806151390075684] [4]
[1, 4] [8, 3, 0] [4.989690780639648] [5]
[1, 5] [9, 10, 0] [5.944950103759766] [6]
[1, 6] [12, 8, 0] [7.017064094543457] [7]
[1, 7] [5, 14, 0] [8.012786865234375] [8]
[1, 8] [15, 15, 0] [9.075039863586426] [9]
[1, 9] [15, 1, 0] [9.97096061706543] [10]
[2, 0] [3, 9, 0] [2.025313377380371] [2]
[2, 1] [3, 6, 0] [2.9828293323516846] [3]
[2, 2] [2, 0, 0] [4.84969615936

[0, 1] [3, 7, 0] [0.9984374046325684] [1]
[0, 2] [0, 3, 0] [3.9965059757232666] [2]
[0, 3] [3, 6, 0] [2.9828293323516846] [3]
[0, 4] [7, 12, 0] [3.989856719970703] [4]
[0, 5] [5, 3, 0] [4.978452682495117] [5]
[0, 6] [9, 4, 0] [5.959085464477539] [6]
[0, 7] [8, 9, 0] [6.995785713195801] [7]
[0, 8] [15, 13, 0] [9.046422958374023] [8]
[0, 9] [14, 2, 0] [8.936978340148926] [9]
[0, 10] [15, 1, 0] [9.97096061706543] [10]
[1, 0] [3, 7, 0] [0.9984374046325684] [1]
[1, 1] [10, 3, 0] [1.9842963218688965] [2]
[1, 2] [3, 1, 0] [3.000070810317993] [3]
[1, 3] [10, 12, 0] [4.001784801483154] [4]
[1, 4] [11, 3, 0] [4.967543601989746] [5]
[1, 5] [13, 3, 0] [5.949042320251465] [6]
[1, 6] [15, 4, 0] [7.031221389770508] [7]
[1, 7] [13, 12, 0] [7.8882646560668945] [8]
[1, 8] [6, 9, 0] [9.01753044128418] [9]
[1, 9] [6, 14, 0] [9.955975532531738] [10]
[2, 0] [10, 3, 0] [1.9842963218688965] [2]
[2, 1] [4, 0, 0] [2.9690911769866943] [3]
[2, 2] [4, 11, 0] [3.9997570514678955] [4]
[2, 3] [11, 3, 0] [4.9675436019

[0, 0] [3, 3, 0] [-0.010573148727416992] [0]
[0, 1] [3, 0, 0] [0.9699199199676514] [1]
[0, 2] [4, 3, 0] [1.9769492149353027] [2]
[0, 3] [4, 10, 0] [2.985368251800537] [3]
[0, 4] [7, 9, 0] [3.992933988571167] [4]
[0, 5] [11, 3, 0] [4.967543601989746] [5]
[0, 6] [9, 7, 0] [5.957056045532227] [6]
[0, 7] [13, 10, 0] [6.895030975341797] [7]
[0, 8] [5, 15, 0] [8.0061616897583] [8]
[0, 9] [5, 1, 0] [9.01511001586914] [9]
[0, 10] [14, 14, 0] [9.943055152893066] [10]
[1, 0] [3, 7, 0] [0.9984374046325684] [1]
[1, 1] [4, 3, 0] [1.9769492149353027] [2]
[1, 2] [4, 0, 0] [2.9690911769866943] [3]
[1, 3] [4, 9, 0] [3.9849562644958496] [4]
[1, 4] [8, 3, 0] [4.989690780639648] [5]
[1, 5] [15, 3, 0] [5.972287178039551] [6]
[1, 6] [9, 2, 0] [6.867505073547363] [7]
[1, 7] [5, 14, 0] [8.012786865234375] [8]
[1, 8] [14, 9, 0] [9.011672973632812] [9]
[1, 9] [9, 1, 0] [9.010052680969238] [10]
[2, 0] [3, 12, 0] [2.0213513374328613] [2]
[2, 1] [4, 4, 0] [2.9911086559295654] [3]
[2, 2] [2, 3, 0] [3.92758011817932

In [257]:
run_n_tests(games30, 20, lambda x: test_all_set(x, 30))


--------
Running tests for game 0
Testing 496 samples of numbers that sum up to 30
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 1] [5, 0] [2.511366844177246] [1]
[0, 2] [0, 0] [2.636687755584717] [2]
[0, 3] [0, 0] [2.636687755584717] [3]
[0, 4] [53, 0] [5.124171257019043] [4]
[0, 5] [53, 0] [5.124171257019043] [5]
[0, 6] [53, 0] [5.124171257019043] [6]
[0, 7] [30, 0] [7.602512359619141] [7]
[0, 8] [30, 0] [7.602512359619141] [8]
[0, 9] [44, 0] [10.19202709197998] [9]
[0, 10] [44, 0] [10.19202709197998] [10]
[0, 11] [44, 0] [10.19202709197998] [11]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 13] [6, 0] [12.983189582824707] [13]
[0, 14] [6, 0] [12.983189582824707] [14]
[0, 15] [6, 0] [12.983189582824707] [15]
[0, 16] [59, 0] [15.310480117797852] [16]
[0, 17] [38, 0] [16.9996395111084] [17]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 19] [46, 0] [19.015756607055664] [19]
[0, 20] [46, 0] [19.015756607055664] [20]
[0, 21] [4, 0] [21.35414695739746] [21]
[0, 22] [4, 0] [21.35414695739746] [22

[8, 1] [30, 0] [7.602512359619141] [9]
[8, 2] [44, 0] [10.19202709197998] [10]
[8, 3] [44, 0] [10.19202709197998] [11]
[8, 4] [44, 0] [10.19202709197998] [12]
[8, 5] [6, 0] [12.983189582824707] [13]
[8, 6] [6, 0] [12.983189582824707] [14]
[8, 7] [6, 0] [12.983189582824707] [15]
[8, 8] [59, 0] [15.310480117797852] [16]
[8, 9] [38, 0] [16.9996395111084] [17]
[8, 10] [38, 0] [16.9996395111084] [18]
[8, 11] [46, 0] [19.015756607055664] [19]
[8, 12] [46, 0] [19.015756607055664] [20]
[8, 13] [4, 0] [21.35414695739746] [21]
[8, 14] [4, 0] [21.35414695739746] [22]
[8, 15] [4, 0] [21.35414695739746] [23]
[8, 16] [26, 0] [23.428987503051758] [24]
[8, 17] [11, 0] [24.879600524902344] [25]
[8, 18] [11, 0] [24.879600524902344] [26]
[8, 19] [49, 0] [27.074626922607422] [27]
[8, 20] [49, 0] [27.074626922607422] [28]
[8, 21] [37, 0] [29.208431243896484] [29]
[8, 22] [37, 0] [29.208431243896484] [30]
[9, 0] [30, 0] [7.602512359619141] [9]
[9, 1] [44, 0] [10.19202709197998] [10]
[9, 2] [44, 0] [10.19202

[5, 15] [46, 0] [19.015756607055664] [20]
[5, 16] [4, 0] [21.35414695739746] [21]
[5, 17] [4, 0] [21.35414695739746] [22]
[5, 18] [4, 0] [21.35414695739746] [23]
[5, 19] [26, 0] [23.428987503051758] [24]
[5, 20] [11, 0] [24.879600524902344] [25]
[5, 21] [11, 0] [24.879600524902344] [26]
[5, 22] [49, 0] [27.074626922607422] [27]
[5, 23] [49, 0] [27.074626922607422] [28]
[5, 24] [49, 0] [27.074626922607422] [29]
[5, 25] [37, 0] [29.208431243896484] [30]
[6, 0] [53, 0] [5.124171257019043] [6]
[6, 1] [30, 0] [7.602512359619141] [7]
[6, 2] [30, 0] [7.602512359619141] [8]
[6, 3] [30, 0] [7.602512359619141] [9]
[6, 4] [44, 0] [10.19202709197998] [10]
[6, 5] [44, 0] [10.19202709197998] [11]
[6, 6] [44, 0] [10.19202709197998] [12]
[6, 7] [6, 0] [12.983189582824707] [13]
[6, 8] [6, 0] [12.983189582824707] [14]
[6, 9] [6, 0] [12.983189582824707] [15]
[6, 10] [59, 0] [15.310480117797852] [16]
[6, 11] [38, 0] [16.9996395111084] [17]
[6, 12] [38, 0] [16.9996395111084] [18]
[6, 13] [46, 0] [19.015756

[0, 0] [0, 0] [2.636687755584717] [0]
[0, 1] [0, 0] [2.636687755584717] [1]
[0, 2] [0, 0] [2.636687755584717] [2]
[0, 3] [0, 0] [2.636687755584717] [3]
[0, 4] [53, 0] [5.124171257019043] [4]
[0, 5] [53, 0] [5.124171257019043] [5]
[0, 6] [53, 0] [5.124171257019043] [6]
[0, 7] [30, 0] [7.602512359619141] [7]
[0, 8] [30, 0] [7.602512359619141] [8]
[0, 9] [44, 0] [10.19202709197998] [9]
[0, 10] [44, 0] [10.19202709197998] [10]
[0, 11] [44, 0] [10.19202709197998] [11]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 13] [6, 0] [12.983189582824707] [13]
[0, 14] [6, 0] [12.983189582824707] [14]
[0, 15] [6, 0] [12.983189582824707] [15]
[0, 16] [59, 0] [15.310480117797852] [16]
[0, 17] [38, 0] [16.9996395111084] [17]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 19] [46, 0] [19.015756607055664] [19]
[0, 20] [46, 0] [19.015756607055664] [20]
[0, 21] [4, 0] [21.35414695739746] [21]
[0, 22] [4, 0] [21.35414695739746] [22]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 24] [26, 0] [23.428987503051758] [24]


[0, 0] [0, 0] [2.636687755584717] [0]
[0, 1] [0, 0] [2.636687755584717] [1]
[0, 2] [5, 0] [2.511366844177246] [2]
[0, 3] [0, 0] [2.636687755584717] [3]
[0, 4] [53, 0] [5.124171257019043] [4]
[0, 5] [53, 0] [5.124171257019043] [5]
[0, 6] [53, 0] [5.124171257019043] [6]
[0, 7] [30, 0] [7.602512359619141] [7]
[0, 8] [30, 0] [7.602512359619141] [8]
[0, 9] [44, 0] [10.19202709197998] [9]
[0, 10] [44, 0] [10.19202709197998] [10]
[0, 11] [44, 0] [10.19202709197998] [11]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 13] [6, 0] [12.983189582824707] [13]
[0, 14] [6, 0] [12.983189582824707] [14]
[0, 15] [6, 0] [12.983189582824707] [15]
[0, 16] [59, 0] [15.310480117797852] [16]
[0, 17] [38, 0] [16.9996395111084] [17]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 19] [46, 0] [19.015756607055664] [19]
[0, 20] [46, 0] [19.015756607055664] [20]
[0, 21] [4, 0] [21.35414695739746] [21]
[0, 22] [4, 0] [21.35414695739746] [22]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 24] [26, 0] [23.428987503051758] [24]


...

[16, 9] [11, 0] [24.879600524902344] [25]
[16, 10] [11, 0] [24.879600524902344] [26]
[16, 11] [49, 0] [27.074626922607422] [27]
[16, 12] [49, 0] [27.074626922607422] [28]
[16, 13] [37, 0] [29.208431243896484] [29]
[16, 14] [37, 0] [29.208431243896484] [30]
[17, 0] [59, 0] [15.310480117797852] [17]
[17, 1] [38, 0] [16.9996395111084] [18]
[17, 2] [46, 0] [19.015756607055664] [19]
[17, 3] [46, 0] [19.015756607055664] [20]
[17, 4] [4, 0] [21.35414695739746] [21]
[17, 5] [4, 0] [21.35414695739746] [22]
[17, 6] [4, 0] [21.35414695739746] [23]
[17, 7] [26, 0] [23.428987503051758] [24]
[17, 8] [11, 0] [24.879600524902344] [25]
[17, 9] [11, 0] [24.879600524902344] [26]
[17, 10] [49, 0] [27.074626922607422] [27]
[17, 11] [49, 0] [27.074626922607422] [28]
[17, 12] [37, 0] [29.208431243896484] [29]
[17, 13] [37, 0] [29.208431243896484] [30]
[18, 0] [38, 0] [16.9996395111084] [18]
[18, 1] [46, 0] [19.015756607055664] [19]
[18, 2] [46, 0] [19.015756607055664] [20]
[18, 3] [4, 0] [21.35414695739746] 

[14, 10] [26, 0] [23.428987503051758] [24]
[14, 11] [11, 0] [24.879600524902344] [25]
[14, 12] [11, 0] [24.879600524902344] [26]
[14, 13] [49, 0] [27.074626922607422] [27]
[14, 14] [49, 0] [27.074626922607422] [28]
[14, 15] [37, 0] [29.208431243896484] [29]
[14, 16] [37, 0] [29.208431243896484] [30]
[15, 0] [6, 0] [12.983189582824707] [15]
[15, 1] [59, 0] [15.310480117797852] [16]
[15, 2] [59, 0] [15.310480117797852] [17]
[15, 3] [38, 0] [16.9996395111084] [18]
[15, 4] [46, 0] [19.015756607055664] [19]
[15, 5] [46, 0] [19.015756607055664] [20]
[15, 6] [4, 0] [21.35414695739746] [21]
[15, 7] [4, 0] [21.35414695739746] [22]
[15, 8] [4, 0] [21.35414695739746] [23]
[15, 9] [26, 0] [23.428987503051758] [24]
[15, 10] [11, 0] [24.879600524902344] [25]
[15, 11] [11, 0] [24.879600524902344] [26]
[15, 12] [49, 0] [27.074626922607422] [27]
[15, 13] [49, 0] [27.074626922607422] [28]
[15, 14] [37, 0] [29.208431243896484] [29]
[15, 15] [37, 0] [29.208431243896484] [30]
[16, 0] [59, 0] [15.3104801177

[12, 18] [37, 0] [29.208431243896484] [30]
[13, 0] [6, 0] [12.983189582824707] [13]
[13, 1] [6, 0] [12.983189582824707] [14]
[13, 2] [6, 0] [12.983189582824707] [15]
[13, 3] [59, 0] [15.310480117797852] [16]
[13, 4] [59, 0] [15.310480117797852] [17]
[13, 5] [38, 0] [16.9996395111084] [18]
[13, 6] [46, 0] [19.015756607055664] [19]
[13, 7] [46, 0] [19.015756607055664] [20]
[13, 8] [4, 0] [21.35414695739746] [21]
[13, 9] [4, 0] [21.35414695739746] [22]
[13, 10] [4, 0] [21.35414695739746] [23]
[13, 11] [26, 0] [23.428987503051758] [24]
[13, 12] [11, 0] [24.879600524902344] [25]
[13, 13] [11, 0] [24.879600524902344] [26]
[13, 14] [49, 0] [27.074626922607422] [27]
[13, 15] [49, 0] [27.074626922607422] [28]
[13, 16] [37, 0] [29.208431243896484] [29]
[13, 17] [37, 0] [29.208431243896484] [30]
[14, 0] [6, 0] [12.983189582824707] [14]
[14, 1] [6, 0] [12.983189582824707] [15]
[14, 2] [59, 0] [15.310480117797852] [16]
[14, 3] [59, 0] [15.310480117797852] [17]
[14, 4] [38, 0] [16.9996395111084] [18

[9, 18] [49, 0] [27.074626922607422] [27]
[9, 19] [49, 0] [27.074626922607422] [28]
[9, 20] [37, 0] [29.208431243896484] [29]
[9, 21] [37, 0] [29.208431243896484] [30]
[10, 0] [44, 0] [10.19202709197998] [10]
[10, 1] [44, 0] [10.19202709197998] [11]
[10, 2] [44, 0] [10.19202709197998] [12]
[10, 3] [6, 0] [12.983189582824707] [13]
[10, 4] [6, 0] [12.983189582824707] [14]
[10, 5] [6, 0] [12.983189582824707] [15]
[10, 6] [59, 0] [15.310480117797852] [16]
[10, 7] [38, 0] [16.9996395111084] [17]
[10, 8] [38, 0] [16.9996395111084] [18]
[10, 9] [46, 0] [19.015756607055664] [19]
[10, 10] [46, 0] [19.015756607055664] [20]
[10, 11] [4, 0] [21.35414695739746] [21]
[10, 12] [4, 0] [21.35414695739746] [22]
[10, 13] [4, 0] [21.35414695739746] [23]
[10, 14] [26, 0] [23.428987503051758] [24]
[10, 15] [11, 0] [24.879600524902344] [25]
[10, 16] [11, 0] [24.879600524902344] [26]
[10, 17] [49, 0] [27.074626922607422] [27]
[10, 18] [49, 0] [27.074626922607422] [28]
[10, 19] [37, 0] [29.208431243896484] [29

[8, 9] [38, 0] [16.9996395111084] [17]
[8, 10] [38, 0] [16.9996395111084] [18]
[8, 11] [46, 0] [19.015756607055664] [19]
[8, 12] [46, 0] [19.015756607055664] [20]
[8, 13] [4, 0] [21.35414695739746] [21]
[8, 14] [4, 0] [21.35414695739746] [22]
[8, 15] [4, 0] [21.35414695739746] [23]
[8, 16] [26, 0] [23.428987503051758] [24]
[8, 17] [11, 0] [24.879600524902344] [25]
[8, 18] [11, 0] [24.879600524902344] [26]
[8, 19] [49, 0] [27.074626922607422] [27]
[8, 20] [49, 0] [27.074626922607422] [28]
[8, 21] [37, 0] [29.208431243896484] [29]
[8, 22] [37, 0] [29.208431243896484] [30]
[9, 0] [30, 0] [7.602512359619141] [9]
[9, 1] [44, 0] [10.19202709197998] [10]
[9, 2] [44, 0] [10.19202709197998] [11]
[9, 3] [44, 0] [10.19202709197998] [12]
[9, 4] [6, 0] [12.983189582824707] [13]
[9, 5] [6, 0] [12.983189582824707] [14]
[9, 6] [6, 0] [12.983189582824707] [15]
[9, 7] [59, 0] [15.310480117797852] [16]
[9, 8] [38, 0] [16.9996395111084] [17]
[9, 9] [38, 0] [16.9996395111084] [18]
[9, 10] [46, 0] [19.01575

Game 0:
{'0_0': {0: ['0,0']}, 
'12_0': {1: ['0,1', '1,0']}, 
'2_0': {2: ['0,2', '1,1', '2,0'], 3: ['0,3', '1,2', '2,1', '3,0']}, 
'15_0': {4: ['0,4', '1,3', '2,2', '3,1', '4,0'], 5: ['0,5', '1,4', '2,3', '3,2', '4,1', '5,0']}, 
'13_0': {6: ['0,6', '1,5', '2,4', '3,3', '4,2', '5,1', '6,0']}, 
'8_0': {7: ['0,7', '1,6', '2,5', '3,4', '4,3', '5,2', '6,1', '7,0']}, 
'5_0': {8: ['0,8', '2,6', '3,5', '4,4', '7,1', '8,0']}, 
'3_0': {9: ['0,9', '1,8', '6,3', '7,2'], 10: ['1,9', '8,2']}, 
'4_0': {10: ['0,10', '2,8', '4,6', '5,5', '9,1']}, 
'1_0': {8: ['1,7', '6,2']}, 
'10_0': {9: ['2,7', '9,0'], 10: ['3,7', '10,0']}, 
'11_0': {9: ['3,6', '4,5'], 10: ['6,4', '7,3']}, 
'6_0': {8: ['5,3']}, 
'7_0': {9: ['5,4']}, 
'14_0': {9: ['8,1']}}
Game 2:
    
'16_0':  0: '0,0', 1: ['0,1', '1,0']
'37_0': {2: ['0,2', '1,1', '2,0']}
'40_0': {3: ['0,3', '2,1']}
'0_0': {4: ['0,4', '3,1']}
'41_0': {5: ['0,5', '1,4']}
'35_0': {6: ['0,6', '5,1']}
'52_0': {7: ['0,7']}
'34_0': {8: ['0,8', '4,4', '8,0']}
'46_0': {9: ['0,9', '6,3', '8,1']}
'13_0': {10: ['0,10', '5,5']}
'33_0': {3: ['1,2']}
'24_0': {4: ['1,3', '2,2', '4,0']}
'5_0': {6: ['1,5']}
'14_0': {7: ['1,6', '7,0']}
'63_0': {8: ['1,7', '3,5', '6,2', '7,1']}, 
'21_0': {9: ['1,8']}, 
'50_0': {10: ['1,9']}, 
'62_0': {5: ['2,3', '4,1']}, 
'56_0': {6: ['2,4']}, 
'53_0': {7: ['2,5', '3,4', '4,3', '5,2']}, 
'58_0': {8: ['2,6'], 9: ['2,7', '5,4', '7,2']}, 
'4_0': {10: ['2,8']}, 
'57_0': {3: ['3,0']}, 
'47_0': {5: ['3,2']}, 
'19_0': {6: ['3,3', '4,2', '6,0']}, 
'22_0': {9: ['3,6']}, 
'25_0': {10: ['3,7', '10,0']}, 
'18_0': {9: ['4,5']}, 
'26_0': {10: ['4,6', '8,2']}, 
'27_0': {5: ['5,0']}, 
'11_0': {8: ['5,3']}, 
'30_0': {7: ['6,1']}, 
'51_0': {10: ['6,4']}, 
'23_0': {10: ['7,3']}, 
'49_0': {9: ['9,0']}, 
'38_0': {10: ['9,1']}}

# Test validation only

In [132]:
run_test(games10, lambda x: test_validation_only(x))


--------
Running test for game 0
[5.0, 3.0] [6, 0] [7.937514305114746] [8.0]
[5.0, 2.0] [13, 0] [5.9192399978637695] [7.0]
[0.0, 10.0] [9, 0] [9.432117462158203] [10.0]
[7.0, 0.0] [8, 0] [6.9772443771362305] [7.0]
[5.0, 0.0] [15, 0] [4.443497180938721] [5.0]
[4.0, 0.0] [15, 0] [4.443497180938721] [4.0]
[0.0, 5.0] [15, 0] [4.443497180938721] [5.0]
[7.0, 3.0] [14, 0] [9.45693588256836] [10.0]
[1.0, 2.0] [2, 0] [2.566126585006714] [3.0]
[1.0, 8.0] [9, 0] [9.432117462158203] [9.0]
[2.0, 8.0] [3, 0] [9.458430290222168] [10.0]
[2.0, 0.0] [2, 0] [2.566126585006714] [2.0]
[4.0, 3.0] [8, 0] [6.9772443771362305] [7.0]
[5.0, 1.0] [13, 0] [5.9192399978637695] [6.0]
Unique outputs: 8: {2.566126585006714, 4.443497180938721, 5.9192399978637695, 6.9772443771362305, 7.937514305114746, 9.432117462158203, 9.45693588256836, 9.458430290222168}
Accuracy: 0.5

--------
Running test for game 1
[5.0, 3.0] [19, 0] [8.028335571289062] [8.0]
[5.0, 2.0] [15, 0] [6.27572774887085] [7.0]
[0.0, 10.0] [30, 0] [9.7045

In [137]:
run_n_tests(games10, 20, lambda x: test_validation_only(x))


--------
Running tests for game 0
[5.0, 3.0] [1, 0] [7.9457550048828125] [8.0]
[5.0, 2.0] [8, 0] [6.9772443771362305] [7.0]
[0.0, 10.0] [14, 0] [9.45693588256836] [10.0]
[7.0, 0.0] [8, 0] [6.9772443771362305] [7.0]
[5.0, 0.0] [15, 0] [4.443497180938721] [5.0]
[4.0, 0.0] [15, 0] [4.443497180938721] [4.0]
[0.0, 5.0] [15, 0] [4.443497180938721] [5.0]
[7.0, 3.0] [7, 0] [9.459736824035645] [10.0]
[1.0, 2.0] [2, 0] [2.566126585006714] [3.0]
[1.0, 8.0] [10, 0] [9.457101821899414] [9.0]
[2.0, 8.0] [4, 0] [9.459233283996582] [10.0]
[2.0, 0.0] [2, 0] [2.566126585006714] [2.0]
[4.0, 3.0] [8, 0] [6.9772443771362305] [7.0]
[5.0, 1.0] [13, 0] [5.9192399978637695] [6.0]
Unique outputs: 9: {2.566126585006714, 4.443497180938721, 5.9192399978637695, 6.9772443771362305, 7.9457550048828125, 9.45693588256836, 9.459736824035645, 9.457101821899414, 9.459233283996582}
Accuracy: 0.5714285969734192
[5.0, 3.0] [5, 0] [7.968204975128174] [8.0]
[5.0, 2.0] [8, 0] [6.9772443771362305] [7.0]
[0.0, 10.0] [3, 0] [9.45

[5.0, 3.0] [39, 0] [8.943808555603027] [8.0]
[5.0, 2.0] [59, 0] [6.894960403442383] [7.0]
[0.0, 10.0] [44, 0] [9.927084922790527] [10.0]
[7.0, 0.0] [52, 0] [6.923108100891113] [7.0]
[5.0, 0.0] [62, 0] [4.935051918029785] [5.0]
[4.0, 0.0] [33, 0] [3.9654130935668945] [4.0]
[0.0, 5.0] [41, 0] [4.90850305557251] [5.0]
[7.0, 3.0] [12, 0] [9.954925537109375] [10.0]
[1.0, 2.0] [40, 0] [2.8636112213134766] [3.0]
[1.0, 8.0] [60, 0] [8.945900917053223] [9.0]
[2.0, 8.0] [38, 0] [9.925065040588379] [10.0]
[2.0, 0.0] [37, 0] [1.8416417837142944] [2.0]
[4.0, 3.0] [28, 0] [7.939607620239258] [7.0]
[5.0, 1.0] [56, 0] [5.885279655456543] [6.0]
Unique outputs: 14: {1.8416417837142944, 2.8636112213134766, 3.9654130935668945, 4.935051918029785, 4.90850305557251, 6.894960403442383, 6.923108100891113, 8.943808555603027, 9.927084922790527, 9.954925537109375, 8.945900917053223, 9.925065040588379, 7.939607620239258, 5.885279655456543}
Accuracy: 0.8571428656578064
[5.0, 3.0] [48, 0] [7.925562858581543] [8.0]
[

[5.0, 3.0] [35, 0] [8.718973159790039] [8.0]
[5.0, 2.0] [113, 0] [7.046563625335693] [7.0]
[0.0, 10.0] [111, 0] [9.710860252380371] [10.0]
[7.0, 0.0] [113, 0] [7.046563625335693] [7.0]
[5.0, 0.0] [116, 0] [5.144576549530029] [5.0]
[4.0, 0.0] [84, 0] [4.1829400062561035] [4.0]
[0.0, 5.0] [116, 0] [5.144576549530029] [5.0]
[7.0, 3.0] [1, 0] [9.611578941345215] [10.0]
[1.0, 2.0] [122, 0] [4.133975505828857] [3.0]
[1.0, 8.0] [59, 0] [8.696344375610352] [9.0]
[2.0, 8.0] [31, 0] [9.710868835449219] [10.0]
[2.0, 0.0] [67, 0] [2.1792752742767334] [2.0]
[4.0, 3.0] [44, 0] [7.04043436050415] [7.0]
[5.0, 1.0] [76, 0] [6.110830783843994] [6.0]
Unique outputs: 12: {2.1792752742767334, 4.1829400062561035, 5.144576549530029, 4.133975505828857, 7.046563625335693, 8.718973159790039, 9.710860252380371, 9.611578941345215, 8.696344375610352, 9.710868835449219, 7.04043436050415, 6.110830783843994}
Accuracy: 0.8571428656578064
[5.0, 3.0] [59, 0] [8.696344375610352] [8.0]
[5.0, 2.0] [113, 0] [7.0465636253356

Unique outputs: 14: {2.0005621910095215, 3.0334155559539795, 4.0373358726501465, 5.013034820556641, 6.961879730224609, 7.096721649169922, 8.07223129272461, 5.0187883377075195, 10.070355415344238, 10.003418922424316, 9.124749183654785, 10.07051944732666, 7.071333885192871, 6.057031631469727}
Accuracy: 1.0
[5.0, 3.0] [1, 3, 0] [8.321381568908691] [8.0]
[5.0, 2.0] [15, 4, 0] [7.127068519592285] [7.0]
[0.0, 10.0] [13, 1, 0] [10.015853881835938] [10.0]
[7.0, 0.0] [13, 10, 0] [6.974566459655762] [7.0]
[5.0, 0.0] [5, 3, 0] [5.024966239929199] [5.0]
[4.0, 0.0] [4, 9, 0] [4.022879600524902] [4.0]
[0.0, 5.0] [2, 10, 0] [4.899632453918457] [5.0]
[7.0, 3.0] [6, 14, 0] [10.014853477478027] [10.0]
[1.0, 2.0] [10, 4, 0] [3.0377285480499268] [3.0]
[1.0, 8.0] [14, 8, 0] [9.114709854125977] [9.0]
[2.0, 8.0] [6, 13, 0] [10.028200149536133] [10.0]
[2.0, 0.0] [10, 3, 0] [2.0005621910095215] [2.0]
[4.0, 3.0] [13, 4, 0] [7.071333885192871] [7.0]
[5.0, 1.0] [5, 7, 0] [6.061479568481445] [6.0]
Unique outputs: 

# Test above number range

In [164]:
start_numbers = [ 11, 13, 21, 101]
end_numbers = [ 12, 20, 100, 100000]
n_samples = [ 10, 100, 100, 1000]
run_test(games10, lambda x: test_various_ranges(x, start_numbers, end_numbers, n_samples))


--------
Running test for game 0
Testing 10 samples of numbers that sum up to [11 - 12]
[4, 7] [10, 0] [9.457101821899414] [11]
[5, 6] [14, 0] [9.45693588256836] [11]
[2, 10] [9, 0] [9.432117462158203] [12]
[11, 1] [3, 0] [9.458430290222168] [12]
[1, 10] [10, 0] [9.457101821899414] [11]
[6, 5] [9, 0] [9.432117462158203] [11]
[8, 4] [9, 0] [9.432117462158203] [12]
[10, 1] [10, 0] [9.457101821899414] [11]
[7, 4] [14, 0] [9.45693588256836] [11]
[0, 11] [7, 0] [9.459736824035645] [11]
Unique outputs: 5: {9.457101821899414, 9.458430290222168, 9.459736824035645, 9.45693588256836, 9.432117462158203}
Accuracy: 0.0
Testing 100 samples of numbers that sum up to [13 - 20]
[12, 2] [7, 0] [9.459736824035645] [14]
[14, 0] [4, 0] [9.459233283996582] [14]
[0, 20] [10, 0] [9.457101821899414] [20]
[16, 3] [11, 0] [9.447063446044922] [19]
[2, 18] [3, 0] [9.458430290222168] [20]
[12, 7] [10, 0] [9.457101821899414] [19]
[12, 8] [14, 0] [9.45693588256836] [20]
[2, 13] [11, 0] [9.447063446044922] [15]
[2, 1

[18353, 41432] [20, 0] [10.1311616897583] [59785]
[1477, 6588] [20, 0] [10.1311616897583] [8065]
[2565, 31227] [20, 0] [10.1311616897583] [33792]
[28733, 2344] [20, 0] [10.1311616897583] [31077]
[18298, 16838] [20, 0] [10.1311616897583] [35136]
[35566, 17138] [20, 0] [10.1311616897583] [52704]
[5206, 10854] [20, 0] [10.1311616897583] [16060]
[47932, 40158] [20, 0] [10.1311616897583] [88090]
[20451, 12154] [12, 0] [10.206038475036621] [32605]
[921, 1487] [18, 0] [9.66733455657959] [2408]
[10502, 48474] [20, 0] [10.1311616897583] [58976]
[12163, 17960] [12, 0] [10.206038475036621] [30123]
[1910, 31590] [20, 0] [10.1311616897583] [33500]
[12903, 60536] [12, 0] [10.206038475036621] [73439]
[19408, 42690] [20, 0] [10.1311616897583] [62098]
[37961, 33550] [20, 0] [10.1311616897583] [71511]
[20248, 37843] [20, 0] [10.1311616897583] [58091]
[1042, 78652] [12, 0] [10.206038475036621] [79694]
[18813, 48172] [20, 0] [10.1311616897583] [66985]
[48478, 11210] [20, 0] [10.1311616897583] [59688]
[214

[7, 14] [2, 0] [9.953782081604004] [21]
[14, 42] [36, 0] [9.95803451538086] [56]
[13, 19] [2, 0] [9.953782081604004] [32]
[14, 12] [25, 0] [9.955145835876465] [26]
[10, 20] [51, 0] [9.95382022857666] [30]
[30, 35] [51, 0] [9.95382022857666] [65]
[8, 73] [36, 0] [9.95803451538086] [81]
[3, 46] [51, 0] [9.95382022857666] [49]
[74, 2] [26, 0] [9.98003101348877] [76]
[8, 13] [51, 0] [9.95382022857666] [21]
[43, 24] [25, 0] [9.955145835876465] [67]
[54, 29] [36, 0] [9.95803451538086] [83]
[7, 60] [2, 0] [9.953782081604004] [67]
[5, 33] [51, 0] [9.95382022857666] [38]
[62, 4] [51, 0] [9.95382022857666] [66]
[37, 29] [36, 0] [9.95803451538086] [66]
[5, 19] [2, 0] [9.953782081604004] [24]
[40, 47] [26, 0] [9.98003101348877] [87]
[37, 14] [36, 0] [9.95803451538086] [51]
[6, 17] [36, 0] [9.95803451538086] [23]
[5, 29] [25, 0] [9.955145835876465] [34]
[13, 77] [36, 0] [9.95803451538086] [90]
[43, 14] [2, 0] [9.953782081604004] [57]
[1, 29] [51, 0] [9.95382022857666] [30]
[4, 69] [26, 0] [9.980031

[20276, 10920] [2, 0] [9.953782081604004] [31196]
[15914, 24194] [26, 0] [9.98003101348877] [40108]
[10164, 2441] [36, 0] [9.95803451538086] [12605]
[1215, 706] [51, 0] [9.95382022857666] [1921]
[7761, 11272] [51, 0] [9.95382022857666] [19033]
[6391, 1907] [36, 0] [9.95803451538086] [8298]
[72697, 20818] [51, 0] [9.95382022857666] [93515]
[34585, 2860] [23, 0] [9.954358100891113] [37445]
[28130, 4595] [51, 0] [9.95382022857666] [32725]
[35316, 21268] [51, 0] [9.95382022857666] [56584]
[17652, 5433] [23, 0] [9.954358100891113] [23085]
[63311, 25879] [51, 0] [9.95382022857666] [89190]
[14009, 63893] [23, 0] [9.954358100891113] [77902]
[15123, 434] [25, 0] [9.955145835876465] [15557]
[1897, 62363] [51, 0] [9.95382022857666] [64260]
[9311, 87133] [51, 0] [9.95382022857666] [96444]
[41891, 40564] [36, 0] [9.95803451538086] [82455]
[10255, 42678] [51, 0] [9.95382022857666] [52933]
[70050, 9753] [36, 0] [9.95803451538086] [79803]
[75326, 20257] [23, 0] [9.954358100891113] [95583]
[685, 489] [

[10666, 38615] [77, 0] [9.574792861938477] [49281]
[2209, 14607] [65, 0] [9.582111358642578] [16816]
[41787, 53708] [77, 0] [9.574792861938477] [95495]
[4161, 86643] [77, 0] [9.574792861938477] [90804]
[4382, 38687] [77, 0] [9.574792861938477] [43069]
[25776, 32090] [77, 0] [9.574792861938477] [57866]
[7112, 18099] [65, 0] [9.582111358642578] [25211]
[27307, 10390] [65, 0] [9.582111358642578] [37697]
[24903, 1448] [77, 0] [9.574792861938477] [26351]
[8090, 26337] [77, 0] [9.574792861938477] [34427]
[5130, 2715] [77, 0] [9.574792861938477] [7845]
[38254, 33630] [77, 0] [9.574792861938477] [71884]
[32213, 59836] [77, 0] [9.574792861938477] [92049]
[2552, 2389] [65, 0] [9.582111358642578] [4941]
[42708, 43883] [77, 0] [9.574792861938477] [86591]
[22425, 74888] [65, 0] [9.582111358642578] [97313]
[52586, 23555] [65, 0] [9.582111358642578] [76141]
[7299, 4279] [65, 0] [9.582111358642578] [11578]
[6040, 1547] [65, 0] [9.582111358642578] [7587]
[26669, 5309] [77, 0] [9.574792861938477] [31978

[11, 39] [1, 15, 0] [10.056402206420898] [50]
[10, 36] [1, 5, 0] [10.039690971374512] [46]
[4, 84] [14, 13, 0] [10.017247200012207] [88]
[12, 27] [1, 2, 0] [10.02303409576416] [39]
[33, 11] [1, 13, 0] [10.059197425842285] [44]
[47, 26] [1, 1, 0] [10.07402229309082] [73]
[4, 35] [13, 1, 0] [10.015853881835938] [39]
[51, 36] [1, 15, 0] [10.056402206420898] [87]
[7, 92] [6, 15, 0] [10.047601699829102] [99]
[3, 83] [1, 12, 0] [10.03320026397705] [86]
[30, 47] [1, 14, 0] [10.07051944732666] [77]
[12, 49] [1, 6, 0] [10.070355415344238] [61]
[31, 34] [1, 6, 0] [10.070355415344238] [65]
[29, 43] [1, 1, 0] [10.07402229309082] [72]
[29, 5] [1, 13, 0] [10.059197425842285] [34]
[26, 1] [1, 6, 0] [10.070355415344238] [27]
[10, 42] [1, 14, 0] [10.07051944732666] [52]
[17, 72] [1, 15, 0] [10.056402206420898] [89]
[51, 9] [1, 8, 0] [10.0302152633667] [60]
[28, 41] [1, 1, 0] [10.07402229309082] [69]
[24, 28] [1, 15, 0] [10.056402206420898] [52]
[4, 41] [1, 1, 0] [10.07402229309082] [45]
[18, 24] [1, 2,

[37659, 10888] [1, 1, 0] [10.07402229309082] [48547]
[12646, 78914] [1, 5, 0] [10.039690971374512] [91560]
[29506, 10934] [1, 6, 0] [10.070355415344238] [40440]
[23955, 30054] [1, 8, 0] [10.0302152633667] [54009]
[4339, 4217] [1, 6, 0] [10.070355415344238] [8556]
[41110, 54622] [13, 1, 0] [10.015853881835938] [95732]
[22485, 46020] [14, 15, 0] [10.041443824768066] [68505]
[9779, 13629] [1, 14, 0] [10.07051944732666] [23408]
[3542, 31379] [1, 5, 0] [10.039690971374512] [34921]
[9374, 54056] [1, 13, 0] [10.059197425842285] [63430]
[41170, 48269] [1, 5, 0] [10.039690971374512] [89439]
[10049, 42756] [1, 1, 0] [10.07402229309082] [52805]
[7199, 54603] [1, 15, 0] [10.056402206420898] [61802]
[48166, 13886] [1, 13, 0] [10.059197425842285] [62052]
[27108, 11800] [1, 15, 0] [10.056402206420898] [38908]
[5024, 74907] [1, 1, 0] [10.07402229309082] [79931]
[12675, 37449] [1, 15, 0] [10.056402206420898] [50124]
[9570, 19314] [14, 6, 0] [10.017226219177246] [28884]
[10868, 57755] [1, 13, 0] [10.059

In [258]:
start_numbers = [ 31, 33, 41, 101]
end_numbers = [ 32, 40, 100, 100000]
n_samples = [ 10, 100, 100, 1000]
run_test(games30, lambda x: test_various_ranges(x, start_numbers, end_numbers, n_samples))


--------
Running test for game 0
Generating 10 samples...
Inputs: [[12, 20], [30, 1], [1, 31], [28, 4], [9, 22], [23, 8], [31, 1], [17, 14], [24, 8], [3, 28]]
Labels: [[32], [31], [32], [32], [31], [31], [32], [31], [32], [31]]
Testing 10 samples of numbers that sum up to [31 - 32]
[12, 20] [34, 0] [30.599462509155273] [32]
[30, 1] [37, 0] [29.208431243896484] [31]
[1, 31] [34, 0] [30.599462509155273] [32]
[28, 4] [34, 0] [30.599462509155273] [32]
[9, 22] [37, 0] [29.208431243896484] [31]
[23, 8] [37, 0] [29.208431243896484] [31]
[31, 1] [34, 0] [30.599462509155273] [32]
[17, 14] [37, 0] [29.208431243896484] [31]
[24, 8] [34, 0] [30.599462509155273] [32]
[3, 28] [37, 0] [29.208431243896484] [31]
Unique outputs: 2: {29.208431243896484, 30.599462509155273}
Accuracy: 0.0
Generating 100 samples...
Inputs: [[21, 16], [33, 3], [31, 7], [20, 17], [28, 7], [24, 12], [24, 16], [11, 25], [29, 5], [32, 7], [11, 29], [32, 8], [13, 21], [6, 27], [6, 31], [14, 26], [31, 2], [35, 3], [3, 35], [23, 1

[19572, 48374] [43, 0] [31.116241455078125] [67946]
[17756, 73586] [43, 0] [31.116241455078125] [91342]
[25654, 66000] [43, 0] [31.116241455078125] [91654]
[6442, 588] [43, 0] [31.116241455078125] [7030]
[70332, 9812] [43, 0] [31.116241455078125] [80144]
[32697, 29965] [43, 0] [31.116241455078125] [62662]
[41822, 41384] [43, 0] [31.116241455078125] [83206]
[14157, 7393] [43, 0] [31.116241455078125] [21550]
[2863, 11041] [43, 0] [31.116241455078125] [13904]
[10453, 37863] [43, 0] [31.116241455078125] [48316]
[15058, 30724] [43, 0] [31.116241455078125] [45782]
[8633, 68910] [43, 0] [31.116241455078125] [77543]
[23242, 24895] [43, 0] [31.116241455078125] [48137]
[29406, 4680] [43, 0] [31.116241455078125] [34086]
[47040, 9391] [43, 0] [31.116241455078125] [56431]
[6247, 2542] [43, 0] [31.116241455078125] [8789]
[45468, 40246] [43, 0] [31.116241455078125] [85714]
[46522, 33339] [43, 0] [31.116241455078125] [79861]
[31434, 18378] [43, 0] [31.116241455078125] [49812]
[23769, 17340] [43, 0] [3

# Test various numbers

In [49]:
run_test(games10, lambda x: test_some_other_numbers(x))


--------
Running test for game 0
[9.0, 0.2] [11, 0] [9.506988525390625] [9.2]
[0.0, 0.3] [12, 0] [0.6395790576934814] [0.3]
[6.0, 4.0] [4, 0] [9.518916130065918] [10.0]
[6.0, 4.0] [7, 0] [9.51953125] [10.0]
[9.0, 1.0] [11, 0] [9.506988525390625] [10.0]
[9.0, 1.0] [10, 0] [9.517173767089844] [10.0]
[9.0, 1.0] [3, 0] [9.518096923828125] [10.0]
[1.0, 1.0] [2, 0] [2.6063244342803955] [2.0]
[1.0, 1.0] [2, 0] [2.6063244342803955] [2.0]
[1.0, 1.0] [2, 0] [2.6063244342803955] [2.0]
[0.0, 1.0] [0, 0] [0.8553138971328735] [1.0]
[0.0, 0.0] [12, 0] [0.6395790576934814] [0.0]
[-1.0, 4.0] [2, 0] [2.6063244342803955] [3.0]
[5.0, -2.0] [2, 0] [2.6063244342803955] [3.0]
[-1.0, 0.0] [0, 0] [0.8553138971328735] [-1.0]
[-2.0, -2.0] [0, 0] [0.8553138971328735] [-4.0]
[-9.0, -1.0] [12, 0] [0.6395790576934814] [-10.0]
[8.0, -3.0] [15, 0] [4.512431621551514] [5.0]
[-10.0, -10.0] [0, 0] [0.8553138971328735] [-20.0]
Unique outputs: 9: {0.6395790576934814, 0.8553138971328735, 2.6063244342803955, 4.5124316215515

[-9.0, -1.0] [3, 3, 0] [0.3242495656013489] [-10.0]
[8.0, -3.0] [8, 3, 0] [5.204380035400391] [5.0]
[-10.0, -10.0] [3, 3, 0] [0.3242494463920593] [-20.0]
Unique outputs: 14: {0.3242495656013489, 1.3564751148223877, 2.621310234069824, 2.4026925563812256, 2.698326587677002, 2.905339479446411, 5.204380035400391, 0.3242494463920593, 8.534836769104004, 9.387617111206055, 9.737249374389648, 9.653635025024414, 9.542710304260254, 9.400053024291992}
Accuracy: 0.5263158082962036

--------
Running test for game 11
[9.0, 0.2] [18, 34, 0] [9.088879585266113] [9.2]
[0.0, 0.3] [47, 24, 0] [0.04041561484336853] [0.3]
[6.0, 4.0] [19, 13, 0] [9.069344520568848] [10.0]
[6.0, 4.0] [18, 16, 0] [9.084503173828125] [10.0]
[9.0, 1.0] [44, 13, 0] [9.053078651428223] [10.0]
[9.0, 1.0] [6, 39, 0] [9.054640769958496] [10.0]
[9.0, 1.0] [16, 44, 0] [9.083727836608887] [10.0]
[1.0, 1.0] [57, 9, 0] [1.996918797492981] [2.0]
[1.0, 1.0] [24, 24, 0] [2.002577543258667] [2.0]
[1.0, 1.0] [55, 47, 0] [2.648716688156128] [2

# Test synonymy

In [246]:
number_range = 10
repeat_times = 100
run_test(games10, lambda x: test_synonymy(x, 10, 100))


--------
Running test for game 0
[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 0] [0, 0] [0.8094069957733154] [0]
[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 0] [0, 0] [0.8094069957733154] [0]
[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 0] [0, 0] [0.8094069957733154] [0]
[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 0] [0, 0] [0.8094069957733154] [0]
[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 0] [0, 0] [0.8094069957733154] [0]
[0, 0] [0, 0] [0.8094069957733154] [0]
[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 0] [0, 0] [0.8094069957733154] [0]
[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 0] [0, 0] [0.8094069957733154] [0]
[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 0] [0, 0] [0.8094069957733154] [0]
[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 0] [12, 0] 

[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 1] [2, 0

[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 0] [2, 0

[2, 6] [1, 0] [8.004281044006348] [8]
[2, 6] [5, 0] [7.999305248260498] [8]
[2, 6] [5, 0] [7.999305248260498] [8]
[2, 6] [6, 0] [7.994237422943115] [8]
[2, 6] [5, 0] [7.999305248260498] [8]
[2, 6] [5, 0] [7.999305248260498] [8]
[2, 6] [1, 0] [8.004281044006348] [8]
[2, 6] [6, 0] [7.994237422943115] [8]
[2, 6] [5, 0] [7.999305248260498] [8]
[2, 6] [5, 0] [7.999305248260498] [8]
[2, 6] [6, 0] [7.994237422943115] [8]
[2, 6] [1, 0] [8.004281044006348] [8]
[2, 6] [1, 0] [8.004281044006348] [8]
[2, 6] [1, 0] [8.004281044006348] [8]
[2, 6] [6, 0] [7.994237422943115] [8]
[2, 6] [6, 0] [7.994237422943115] [8]
[2, 6] [5, 0] [7.999305248260498] [8]
[2, 6] [5, 0] [7.999305248260498] [8]
[2, 6] [6, 0] [7.994237422943115] [8]
[2, 6] [6, 0] [7.994237422943115] [8]
[2, 6] [5, 0] [7.999305248260498] [8]
[2, 6] [5, 0] [7.999305248260498] [8]
[2, 6] [1, 0] [8.004281044006348] [8]
[2, 6] [5, 0] [7.999305248260498] [8]
[2, 6] [1, 0] [8.004281044006348] [8]
[2, 6] [5, 0] [7.999305248260498] [8]
[2, 6] [5, 0

[3, 1] [15, 0] [4.509095191955566] [4]
[3, 1] [15, 0] [4.509095191955566] [4]
Unique outputs: 1: {4.509095191955566}
Accuracy: 0.0
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [13, 0] [5.983450889587402] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [13, 0] [5.983450889587402] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [13,

...

[5, 3] [14, 7, 0] [7.903393745422363] [8]
[5, 3] [14, 0, 0] [7.990660667419434] [8]
[5, 3] [6, 4, 0] [7.963973045349121] [8]
[5, 3] [8, 6, 0] [8.016589164733887] [8]
[5, 3] [9, 15, 0] [7.998380661010742] [8]
[5, 3] [15, 9, 0] [7.977939605712891] [8]
[5, 3] [5, 13, 0] [8.02262020111084] [8]
[5, 3] [14, 10, 0] [7.868620872497559] [8]
[5, 3] [11, 15, 0] [8.003278732299805] [8]
[5, 3] [9, 13, 0] [8.012567520141602] [8]
[5, 3] [11, 13, 0] [8.0176420211792] [8]
[5, 3] [15, 9, 0] [7.977939605712891] [8]
[5, 3] [13, 12, 0] [7.8882646560668945] [8]
[5, 3] [8, 13, 0] [8.030757904052734] [8]
[5, 3] [5, 13, 0] [8.02262020111084] [8]
[5, 3] [8, 13, 0] [8.030757904052734] [8]
[5, 3] [5, 13, 0] [8.02262020111084] [8]
[5, 3] [6, 7, 0] [7.908379554748535] [8]
[5, 3] [5, 6, 0] [8.014591217041016] [8]
[5, 3] [6, 7, 0] [7.908379554748535] [8]
[5, 3] [12, 14, 0] [8.010647773742676] [8]
[5, 3] [12, 13, 0] [8.016786575317383] [8]
[5, 3] [6, 10, 0] [7.859598159790039] [8]
[5, 3] [2, 1, 0] [8.114663124084473] 

[6, 1] [15, 0, 0] [7.011680603027344] [7]
[6, 1] [13, 7, 0] [6.944392204284668] [7]
[6, 1] [11, 11, 0] [7.015253067016602] [7]
[6, 1] [15, 0, 0] [7.011680603027344] [7]
[6, 1] [2, 6, 0] [7.079282760620117] [7]
[6, 1] [15, 7, 0] [7.000633239746094] [7]
[6, 1] [13, 4, 0] [6.9732513427734375] [7]
[6, 1] [14, 3, 0] [6.808786392211914] [7]
[6, 1] [2, 13, 0] [7.011425018310547] [7]
[6, 1] [9, 8, 0] [7.010146141052246] [7]
[6, 1] [9, 5, 0] [7.007552146911621] [7]
[6, 1] [13, 0, 0] [6.9571428298950195] [7]
[6, 1] [15, 0, 0] [7.011680603027344] [7]
[6, 1] [11, 12, 0] [6.994004249572754] [7]
[6, 1] [13, 4, 0] [6.9732513427734375] [7]
[6, 1] [13, 4, 0] [6.9732513427734375] [7]
[6, 1] [13, 10, 0] [6.895030975341797] [7]
[6, 1] [6, 3, 0] [6.828197479248047] [7]
[6, 1] [5, 8, 0] [7.026211738586426] [7]
[6, 1] [6, 3, 0] [6.828197479248047] [7]
[6, 1] [5, 5, 0] [7.021413803100586] [7]
[6, 1] [13, 7, 0] [6.944392204284668] [7]
[6, 1] [15, 4, 0] [7.031221389770508] [7]
[6, 1] [11, 8, 0] [7.0204372406005

[7, 3] [14, 14, 0] [9.943055152893066] [10]
[7, 3] [13, 1, 0] [9.968000411987305] [10]
[7, 3] [13, 1, 0] [9.968000411987305] [10]
[7, 3] [15, 1, 0] [9.97096061706543] [10]
[7, 3] [14, 6, 0] [9.959580421447754] [10]
[7, 3] [15, 1, 0] [9.97096061706543] [10]
[7, 3] [1, 2, 0] [9.971314430236816] [10]
[7, 3] [6, 1, 0] [9.98089599609375] [10]
[7, 3] [15, 1, 0] [9.97096061706543] [10]
[7, 3] [14, 6, 0] [9.959580421447754] [10]
[7, 3] [1, 5, 0] [9.989474296569824] [10]
[7, 3] [14, 14, 0] [9.943055152893066] [10]
[7, 3] [15, 1, 0] [9.97096061706543] [10]
[7, 3] [6, 14, 0] [9.955975532531738] [10]
[7, 3] [1, 13, 0] [10.010969161987305] [10]
[7, 3] [15, 1, 0] [9.97096061706543] [10]
[7, 3] [15, 1, 0] [9.97096061706543] [10]
[7, 3] [13, 1, 0] [9.968000411987305] [10]
[7, 3] [13, 1, 0] [9.968000411987305] [10]
[7, 3] [1, 1, 0] [10.025901794433594] [10]
[7, 3] [6, 1, 0] [9.98089599609375] [10]
[7, 3] [1, 15, 0] [10.008197784423828] [10]
[7, 3] [1, 5, 0] [9.989474296569824] [10]
[7, 3] [1, 9, 0] [9.

Unique outputs: 28: {8.944098472595215, 9.024213790893555, 9.970531463623047, 8.969452857971191, 8.895816802978516, 9.032747268676758, 9.01753044128418, 9.046422958374023, 8.964508056640625, 9.006288528442383, 9.020994186401367, 8.992080688476562, 8.993766784667969, 8.960977554321289, 8.946285247802734, 8.936978340148926, 9.012248992919922, 9.020797729492188, 9.039295196533203, 9.01511001586914, 9.01276683807373, 9.014720916748047, 9.010052680969238, 9.011672973632812, 9.032635688781738, 9.035449981689453, 8.95889949798584, 9.075039863586426}
Accuracy: 0.9900000095367432
[9, 1] [1, 13, 0] [10.010969161987305] [10]
[9, 1] [15, 1, 0] [9.97096061706543] [10]
[9, 1] [1, 6, 0] [10.021651268005371] [10]
[9, 1] [6, 6, 0] [9.969858169555664] [10]
[9, 1] [13, 1, 0] [9.968000411987305] [10]
[9, 1] [14, 13, 0] [9.9579439163208] [10]
[9, 1] [14, 15, 0] [9.987500190734863] [10]
[9, 1] [14, 6, 0] [9.959580421447754] [10]
[9, 1] [6, 13, 0] [9.970531463623047] [10]
[9, 1] [6, 13, 0] [9.970531463623047

14_10_0	22
2_13_0	11
9_14_0	20
2_6_0	19
11_14_0	19
11_1_0	47
10_4_0	22
2_7_0	16
11_15_0	26
7_7_0	28
15_4_0	31
12_6_0	24
8_4_0	39
15_1_0	182
9_3_0	86
7_5_0	13
5_11_0	10
14_11_0	29
3_3_0	100
3_6_0	27
10_14_0	10
14_0_0	26
14_13_0	59
6_9_0	21
13_10_0	19
6_15_0	36
14_1_0	31
15_15_0	29
3_1_0	9
4_6_0	18
10_8_0	8
9_12_0	15
15_10_0	31
5_14_0	35
12_2_0	16
4_2_0	14
12_14_0	30
10_5_0	15
4_10_0	32
3_8_0	19
4_12_0	14
6_0_0	24
8_8_0	12
7_4_0	26
7_2_0	7
4_7_0	16
4_15_0	15
13_6_0	40
4_13_0	20
10_11_0	10
10_9_0	10
5_9_0	13
14_2_0	19
10_0_0	22
14_5_0	25
4_9_0	15
14_6_0	53
5_7_0	21
12_8_0	7
10_10_0	24
9_15_0	24
13_12_0	10
15_5_0	7
5_12_0	14
1_15_0	46
15_8_0	17
8_1_0	69
13_8_0	12
12_12_0	16
12_13_0	26
12_0_0	34
12_9_0	16
13_13_0	38
6_14_0	56
8_9_0	9
3_2_0	6
15_2_0	8
3_7_0	49
6_6_0	50
2_0_0	16
11_8_0	19
1_13_0	48
8_14_0	29
9_4_0	17
13_2_0	10
11_0_0	14
11_7_0	28
12_15_0	24
2_12_0	12
6_10_0	20
11_4_0	32
13_9_0	18
8_15_0	17
10_7_0	34
3_12_0	12
8_7_0	23
7_13_0	6
13_3_0	69
14_15_0	36
1_12_0	15
1_14_0	27
12_3_0	9

In [242]:
number_range = 10
repeat_times = 100
run_test(games10, lambda x: test_synonymy(x, 10, 10))


--------
Running test for game 0
[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 0] [0, 0] [0.8094069957733154] [0]
[0, 0] [0, 0] [0.8094069957733154] [0]
[0, 0] [0, 0] [0.8094069957733154] [0]
[0, 0] [0, 0] [0.8094069957733154] [0]
[0, 0] [0, 0] [0.8094069957733154] [0]
[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 0] [12, 0] [0.6528407335281372] [0]
Unique outputs: 2: {0.6528407335281372, 0.8094069957733154}
Accuracy: 0.0
[0, 1] [0, 0] [0.8094069957733154] [1]
[0, 1] [12, 0] [0.6528407335281372] [1]
[0, 1] [0, 0] [0.8094069957733154] [1]
[0, 1] [12, 0] [0.6528407335281372] [1]
[0, 1] [0, 0] [0.8094069957733154] [1]
[0, 1] [0, 0] [0.8094069957733154] [1]
[0, 1] [12, 0] [0.6528407335281372] [1]
[0, 1] [12, 0] [0.6528407335281372] [1]
[0, 1] [12, 0] [0.6528407335281372] [1]
[0, 1] [0, 0] [0.8094069957733154] [1]
Unique outputs: 2: {0.8094069957733154, 0.6528407335281372}
Accuracy: 1.0
[0, 2] [2, 0] [2.61378860473

[3, 1] [15, 0] [4.509095191955566] [4]
[3, 1] [15, 0] [4.509095191955566] [4]
[3, 1] [15, 0] [4.509095191955566] [4]
[3, 1] [15, 0] [4.509095191955566] [4]
[3, 1] [15, 0] [4.509095191955566] [4]
[3, 1] [15, 0] [4.509095191955566] [4]
[3, 1] [15, 0] [4.509095191955566] [4]
[3, 1] [15, 0] [4.509095191955566] [4]
[3, 1] [15, 0] [4.509095191955566] [4]
[3, 1] [15, 0] [4.509095191955566] [4]
Unique outputs: 1: {4.509095191955566}
Accuracy: 0.0
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [13, 0] [5.983450889587402] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
[3, 2] [15, 0] [4.509095191955566] [5]
Unique outputs: 2: {4.509095191955566, 5.983450889587402}
Accuracy: 0.8999999761581421
[3, 3] [13, 0] [5.983450889587402] [6]
[3, 3] [13, 0] [5.983450889587402] [6]
[3

[8, 1] [10, 0] [9.49882698059082] [9]
[8, 1] [14, 0] [9.49847412109375] [9]
[8, 1] [4, 0] [9.500732421875] [9]
[8, 1] [3, 0] [9.499813079833984] [9]
[8, 1] [9, 0] [9.471212387084961] [9]
[8, 1] [10, 0] [9.49882698059082] [9]
[8, 1] [3, 0] [9.499813079833984] [9]
[8, 1] [9, 0] [9.471212387084961] [9]
[8, 1] [10, 0] [9.49882698059082] [9]
[8, 1] [7, 0] [9.501371383666992] [9]
Unique outputs: 6: {9.49882698059082, 9.499813079833984, 9.471212387084961, 9.49847412109375, 9.500732421875, 9.501371383666992}
Accuracy: 0.800000011920929
[8, 2] [14, 0] [9.49847412109375] [10]
[8, 2] [9, 0] [9.471212387084961] [10]
[8, 2] [14, 0] [9.49847412109375] [10]
[8, 2] [14, 0] [9.49847412109375] [10]
[8, 2] [3, 0] [9.499813079833984] [10]
[8, 2] [9, 0] [9.471212387084961] [10]
[8, 2] [10, 0] [9.49882698059082] [10]
[8, 2] [7, 0] [9.501371383666992] [10]
[8, 2] [3, 0] [9.499813079833984] [10]
[8, 2] [11, 0] [9.48766803741455] [10]
Unique outputs: 6: {9.49847412109375, 9.49882698059082, 9.501371383666992, 9

[2, 4] [10, 0] [6.617605209350586] [6]
[2, 4] [0, 0] [6.379913330078125] [6]
[2, 4] [10, 0] [6.617605209350586] [6]
[2, 4] [0, 0] [6.379913330078125] [6]
[2, 4] [31, 0] [5.3101911544799805] [6]
[2, 4] [13, 0] [5.307830810546875] [6]
[2, 4] [13, 0] [5.307830810546875] [6]
[2, 4] [10, 0] [6.617605209350586] [6]
[2, 4] [27, 0] [6.567420482635498] [6]
[2, 4] [0, 0] [6.379913330078125] [6]
Unique outputs: 5: {5.307830810546875, 6.567420482635498, 5.3101911544799805, 6.617605209350586, 6.379913330078125}
Accuracy: 0.30000001192092896
[2, 5] [15, 0] [6.261562347412109] [7]
[2, 5] [27, 0] [6.567420482635498] [7]
[2, 5] [0, 0] [6.379913330078125] [7]
[2, 5] [15, 0] [6.261562347412109] [7]
[2, 5] [27, 0] [6.567420482635498] [7]
[2, 5] [0, 0] [6.379913330078125] [7]
[2, 5] [24, 0] [7.369512557983398] [7]
[2, 5] [22, 0] [7.335894584655762] [7]
[2, 5] [10, 0] [6.617605209350586] [7]
[2, 5] [10, 0] [6.617605209350586] [7]
Unique outputs: 6: {6.379913330078125, 7.335894584655762, 7.369512557983398, 6

[5, 1] [2, 0] [5.274763107299805] [6]
[5, 1] [31, 0] [5.3101911544799805] [6]
[5, 1] [0, 0] [6.379913330078125] [6]
[5, 1] [0, 0] [6.379913330078125] [6]
[5, 1] [10, 0] [6.617605209350586] [6]
[5, 1] [10, 0] [6.617605209350586] [6]
[5, 1] [28, 0] [5.705613136291504] [6]
[5, 1] [2, 0] [5.274763107299805] [6]
[5, 1] [10, 0] [6.617605209350586] [6]
[5, 1] [15, 0] [6.261562347412109] [6]
Unique outputs: 6: {5.3101911544799805, 5.705613136291504, 5.274763107299805, 6.379913330078125, 6.617605209350586, 6.261562347412109}
Accuracy: 0.4000000059604645
[5, 2] [0, 0] [6.379913330078125] [7]
[5, 2] [10, 0] [6.617605209350586] [7]
[5, 2] [15, 0] [6.261562347412109] [7]
[5, 2] [22, 0] [7.335894584655762] [7]
[5, 2] [10, 0] [6.617605209350586] [7]
[5, 2] [15, 0] [6.261562347412109] [7]
[5, 2] [0, 0] [6.379913330078125] [7]
[5, 2] [27, 0] [6.567420482635498] [7]
[5, 2] [17, 0] [7.702888488769531] [7]
[5, 2] [0, 0] [6.379913330078125] [7]
Unique outputs: 6: {6.567420482635498, 6.261562347412109, 7.33

...

[6, 0] [43, 0] [5.789170742034912] [6]
[6, 0] [43, 0] [5.789170742034912] [6]
[6, 0] [113, 0] [6.754367351531982] [6]
[6, 0] [43, 0] [5.789170742034912] [6]
[6, 0] [43, 0] [5.789170742034912] [6]
[6, 0] [78, 0] [5.729968547821045] [6]
[6, 0] [43, 0] [5.789170742034912] [6]
[6, 0] [78, 0] [5.729968547821045] [6]
[6, 0] [44, 0] [6.823071479797363] [6]
[6, 0] [76, 0] [5.753654956817627] [6]
Unique outputs: 5: {5.729968547821045, 5.753654956817627, 5.789170742034912, 6.754367351531982, 6.823071479797363}
Accuracy: 0.800000011920929
[6, 1] [119, 0] [7.840209484100342] [7]
[6, 1] [119, 0] [7.840209484100342] [7]
[6, 1] [113, 0] [6.754367351531982] [7]
[6, 1] [119, 0] [7.840209484100342] [7]
[6, 1] [113, 0] [6.754367351531982] [7]
[6, 1] [119, 0] [7.840209484100342] [7]
[6, 1] [113, 0] [6.754367351531982] [7]
[6, 1] [44, 0] [6.823071479797363] [7]
[6, 1] [113, 0] [6.754367351531982] [7]
[6, 1] [95, 0] [7.835409164428711] [7]
Unique outputs: 4: {6.823071479797363, 7.835409164428711, 6.75436735

[0, 2] [4, 3, 0] [1.9769492149353027] [2]
[0, 2] [10, 3, 0] [1.9842963218688965] [2]
[0, 2] [4, 3, 0] [1.9769492149353027] [2]
[0, 2] [4, 3, 0] [1.9769492149353027] [2]
[0, 2] [7, 3, 0] [1.9896314144134521] [2]
[0, 2] [10, 3, 0] [1.9842963218688965] [2]
[0, 2] [4, 3, 0] [1.9769492149353027] [2]
[0, 2] [4, 3, 0] [1.9769492149353027] [2]
[0, 2] [10, 3, 0] [1.9842963218688965] [2]
[0, 2] [10, 3, 0] [1.9842963218688965] [2]
Unique outputs: 3: {1.9769492149353027, 1.9842963218688965, 1.9896314144134521}
Accuracy: 1.0
[0, 3] [3, 15, 0] [2.950218915939331] [3]
[0, 3] [7, 10, 0] [2.994760751724243] [3]
[0, 3] [7, 10, 0] [2.994760751724243] [3]
[0, 3] [7, 7, 0] [2.992901086807251] [3]
[0, 3] [4, 10, 0] [2.985368251800537] [3]
[0, 3] [7, 0, 0] [3.0012753009796143] [3]
[0, 3] [10, 4, 0] [3.0019564628601074] [3]
[0, 3] [10, 7, 0] [2.9980263710021973] [3]
[0, 3] [10, 0, 0] [3.0198147296905518] [3]
[0, 3] [10, 4, 0] [3.0019564628601074] [3]
Unique outputs: 8: {2.992901086807251, 2.985368251800537, 2

Unique outputs: 10: {6.9571428298950195, 7.020437240600586, 7.011680603027344, 6.808786392211914, 7.021413803100586, 7.010146141052246, 6.888580322265625, 6.985201835632324, 6.994004249572754, 6.89164924621582}
Accuracy: 1.0
[1, 7] [5, 14, 0] [8.012786865234375] [8]
[1, 7] [11, 6, 0] [8.013800621032715] [8]
[1, 7] [5, 15, 0] [8.0061616897583] [8]
[1, 7] [9, 6, 0] [8.011096000671387] [8]
[1, 7] [14, 10, 0] [7.868620872497559] [8]
[1, 7] [11, 13, 0] [8.0176420211792] [8]
[1, 7] [13, 8, 0] [7.916558265686035] [8]
[1, 7] [13, 11, 0] [7.904308319091797] [8]
[1, 7] [14, 0, 0] [7.990660667419434] [8]
[1, 7] [13, 2, 0] [7.897315979003906] [8]
Unique outputs: 10: {7.868620872497559, 8.012786865234375, 8.013800621032715, 8.0061616897583, 8.011096000671387, 8.0176420211792, 7.916558265686035, 7.904308319091797, 7.990660667419434, 7.897315979003906}
Accuracy: 1.0
[1, 8] [13, 14, 0] [8.944098472595215] [9]
[1, 8] [14, 12, 0] [9.014720916748047] [9]
[1, 8] [14, 9, 0] [9.011672973632812] [9]
[1, 8] [

Unique outputs: 8: {5.972823143005371, 5.959073066711426, 5.961175918579102, 5.972287178039551, 5.980649948120117, 5.959085464477539, 5.957056045532227, 5.947325706481934}
Accuracy: 1.0
[3, 4] [12, 8, 0] [7.017064094543457] [7]
[3, 4] [14, 3, 0] [6.808786392211914] [7]
[3, 4] [11, 11, 0] [7.015253067016602] [7]
[3, 4] [14, 3, 0] [6.808786392211914] [7]
[3, 4] [12, 5, 0] [7.015412330627441] [7]
[3, 4] [15, 0, 0] [7.011680603027344] [7]
[3, 4] [8, 9, 0] [6.995785713195801] [7]
[3, 4] [2, 6, 0] [7.079282760620117] [7]
[3, 4] [13, 10, 0] [6.895030975341797] [7]
[3, 4] [8, 12, 0] [7.00452995300293] [7]
Unique outputs: 9: {6.808786392211914, 7.011680603027344, 7.015253067016602, 7.015412330627441, 7.017064094543457, 6.995785713195801, 7.079282760620117, 6.895030975341797, 7.00452995300293}
Accuracy: 1.0
[3, 5] [12, 6, 0] [8.012249946594238] [8]
[3, 5] [1, 0, 0] [8.895816802978516] [8]
[3, 5] [15, 8, 0] [8.016416549682617] [8]
[3, 5] [13, 8, 0] [7.916558265686035] [8]
[3, 5] [6, 10, 0] [7.859

[6, 3] [14, 5, 0] [9.032635688781738] [9]
[6, 3] [13, 15, 0] [8.993766784667969] [9]
[6, 3] [13, 13, 0] [8.974340438842773] [9]
[6, 3] [13, 14, 0] [8.944098472595215] [9]
[6, 3] [1, 4, 0] [8.969452857971191] [9]
[6, 3] [15, 6, 0] [9.006288528442383] [9]
[6, 3] [1, 4, 0] [8.969452857971191] [9]
[6, 3] [11, 1, 0] [9.01276683807373] [9]
[6, 3] [14, 9, 0] [9.011672973632812] [9]
[6, 3] [15, 15, 0] [9.075039863586426] [9]
Unique outputs: 9: {8.993766784667969, 9.032635688781738, 8.969452857971191, 8.974340438842773, 8.944098472595215, 9.006288528442383, 9.01276683807373, 9.011672973632812, 9.075039863586426}
Accuracy: 1.0
[6, 4] [13, 1, 0] [9.968000411987305] [10]
[6, 4] [14, 13, 0] [9.9579439163208] [10]
[6, 4] [13, 1, 0] [9.968000411987305] [10]
[6, 4] [14, 15, 0] [9.987500190734863] [10]
[6, 4] [1, 13, 0] [10.010969161987305] [10]
[6, 4] [6, 14, 0] [9.955975532531738] [10]
[6, 4] [15, 1, 0] [9.97096061706543] [10]
[6, 4] [1, 13, 0] [10.010969161987305] [10]
[6, 4] [1, 5, 0] [9.9894742965

In [259]:
run_test(games30, lambda x: test_synonymy(x, 30, 100))


--------
Running test for game 0
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [5, 0] [2.511366844177246] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [5, 0] [2.511366844177246] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [0, 0] [2.636687755584717] [0]
[0, 0] [5, 0] [2

[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] [10.19202709197998] [12]
[0, 12] [44, 0] 

[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
[0, 18] [38, 0] [16.9996395111084] [18]
Unique outputs: 1: {16.9996395111084}
Ac

[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]
[0, 23] [4, 0] [21.35414695739746] [23]


[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.074626922607422] [29]
[0, 29] [49, 0] [27.07462692260742

...

[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.879600524902344] [26]
[25, 1] [11, 0] [24.87960052490234

[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.074626922607422] [28]
[25, 3] [49, 0] [27.07462692260742

[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.074626922607422] [27]
[26, 1] [49, 0] [27.07462692260742

[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.074626922607422] [28]
[27, 1] [49, 0] [27.07462692260742

[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.208431243896484] [30]
[30, 0] [37, 0] [29.20843124389648

game 2:
    
    {'16_0': 5, '37_0': 5, '40_0': 9, '57_0': 9, '0_0': 16, '33_0': 14, '62_0': 19, '24_0': 14, '27_0': 14, '19_0': 24, '56_0': 24, '35_0': 24, '47_0': 12, '5_0': 24, '41_0': 12, '3_0': 24, '14_0': 18, '59_0': 18, '53_0': 18, '6_0': 18, '52_0': 28, '45_0': 40, '28_0': 27, '30_0': 17, '34_0': 40, '63_0': 40, '11_0': 27, '29_0': 40, '58_0': 43, '61_0': 30, '18_0': 43, '55_0': 30, '22_0': 43, '54_0': 43, '48_0': 30, '9_0': 30, '1_0': 17, '39_0': 30, '60_0': 39, '49_0': 26, '43_0': 26, '38_0': 39, '7_0': 39, '21_0': 39, '46_0': 39, '13_0': 39, '42_0': 39, '31_0': 39, '8_0': 39, '10_0': 39, '15_0': 39, '32_0': 28, '26_0': 28, '23_0': 28, '51_0': 28, '50_0': 28, '20_0': 28, '25_0': 28, '12_0': 28, '2_0': 28, '36_0': 28, '17_0': 28, '44_0': 28, '4_0': 28}
Each message frequency
45_0	88
55_0	55
28_0	45
60_0	66
22_0	59
32_0	67
62_0	232
54_0	75
49_0	48
34_0	87
43_0	14
5_0	184
16_0	250
26_0	105
23_0	135
51_0	60
59_0	66
56_0	226
14_0	106
50_0	57
47_0	52
7_0	61
38_0	81
57_0	124
27_0	76
21_0	101
9_0	36
63_0	134
0_0	122
46_0	48
10_0	85
52_0	115
13_0	96
29_0	120
33_0	263
35_0	113
61_0	49
18_0	84
20_0	73
30_0	90
53_0	275
25_0	61
24_0	166
12_0	51
6_0	127
48_0	91
2_0	73
37_0	329
42_0	54
36_0	61
41_0	176
3_0	88
58_0	89
19_0	157
31_0	20
17_0	34
40_0	254
8_0	57
44_0	31
1_0	171
11_0	119
4_0	24
15_0	55
39_0	89
Total messages 6600, Unique messages: 64
Unique messages per labels: {0: 4, 1: 5, 2: 3, 3: 6, 4: 7, 5: 12, 6: 11, 7: 17, 8: 17, 9: 26, 10: 28}

In [252]:
test_all_set(games10[0], 10)

Testing 66 samples of numbers that sum up to 10
[0, 0] [0, 0] [0.8094069957733154] [0]
[0, 1] [12, 0] [0.6528407335281372] [1]
[0, 2] [2, 0] [2.613788604736328] [2]
[0, 3] [2, 0] [2.613788604736328] [3]
[0, 4] [15, 0] [4.509095191955566] [4]
[0, 5] [15, 0] [4.509095191955566] [5]
[0, 6] [13, 0] [5.983450889587402] [6]
[0, 7] [8, 0] [7.006291389465332] [7]
[0, 8] [5, 0] [7.999305248260498] [8]
[0, 9] [9, 0] [9.471212387084961] [9]
[0, 10] [7, 0] [9.501371383666992] [10]
[1, 0] [0, 0] [0.8094069957733154] [1]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 2] [2, 0] [2.613788604736328] [3]
[1, 3] [15, 0] [4.509095191955566] [4]
[1, 4] [15, 0] [4.509095191955566] [5]
[1, 5] [13, 0] [5.983450889587402] [6]
[1, 6] [8, 0] [7.006291389465332] [7]
[1, 7] [5, 0] [7.999305248260498] [8]
[1, 8] [11, 0] [9.48766803741455] [9]
[1, 9] [7, 0] [9.501371383666992] [10]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 1] [2, 0] [2.613788604736328] [3]
[2, 2] [15, 0] [4.509095191955566] [4]
[2, 3] [15, 0] [4.50909519

(0.7575757503509521,
 16,
 [13, 0.8125, 0.19696969696969696, 8, 0.5, 0.5757575757575757])

In [253]:
test_all_set(games10[0], 10)

Testing 66 samples of numbers that sum up to 10
[0, 0] [12, 0] [0.6528407335281372] [0]
[0, 1] [0, 0] [0.8094069957733154] [1]
[0, 2] [2, 0] [2.613788604736328] [2]
[0, 3] [2, 0] [2.613788604736328] [3]
[0, 4] [15, 0] [4.509095191955566] [4]
[0, 5] [15, 0] [4.509095191955566] [5]
[0, 6] [13, 0] [5.983450889587402] [6]
[0, 7] [8, 0] [7.006291389465332] [7]
[0, 8] [1, 0] [8.004281044006348] [8]
[0, 9] [4, 0] [9.500732421875] [9]
[0, 10] [11, 0] [9.48766803741455] [10]
[1, 0] [12, 0] [0.6528407335281372] [1]
[1, 1] [2, 0] [2.613788604736328] [2]
[1, 2] [2, 0] [2.613788604736328] [3]
[1, 3] [15, 0] [4.509095191955566] [4]
[1, 4] [15, 0] [4.509095191955566] [5]
[1, 5] [13, 0] [5.983450889587402] [6]
[1, 6] [8, 0] [7.006291389465332] [7]
[1, 7] [6, 0] [7.994237422943115] [8]
[1, 8] [11, 0] [9.48766803741455] [9]
[1, 9] [14, 0] [9.49847412109375] [10]
[2, 0] [2, 0] [2.613788604736328] [2]
[2, 1] [2, 0] [2.613788604736328] [3]
[2, 2] [15, 0] [4.509095191955566] [4]
[2, 3] [15, 0] [4.5090951919

(0.6666666865348816,
 16,
 [15, 0.9375, 0.22727272727272727, 8, 0.5, 0.5909090909090908])

---

In [104]:
def load_run(epochs, last_save, model_size, model_number, run_number, vocab, sender, receiver, embedding, length=1):
    epochs = epochs
    save_name = "game/models/game{}_{}_{}_{}_{}_{}_{}".format(model_size, model_number, run_number, vocab, sender, receiver, embedding)
    if(length > 1):
        save_name = "{}_{}".format(save_name, length)
    

    params = [
        '--batch_size=1',
        '--n_epochs={}'.format(epochs),
        '--vocab_size={}'.format(vocab),
        '--sender_hidden={}'.format(sender),
        '--receiver_hidden={}'.format(receiver),
        '--lr=0.001',
        '--max_len={}'.format(length),
        '--sender_entropy=0.5',
        '--sender_embedding={}'.format(embedding),
        '--receiver_embedding={}'.format(embedding),
        '--validation_freq=10',
        '--train_data=game/data/train10.txt',
        '--validation_data=game/data/validation10.txt',
    ]
    if(last_save > 0):
        params.append('--load_from_checkpoint={}_{}.tar'.format(save_name, last_save))
        
    game = Game(params)
    game.play()
    game.save_checkpoint(epochs, save_name)
    return game

In [105]:

#Checkpoint saved at game/models/game10_14_1_128_128_128_8_1500.tar
load_run(1, 0, 10, 14, 1, 128, 128, 128, 8)

Preparing dataset...
Samples in training set: 52
Samples in test set: 14

----------
Building model...
SenderReceiverRnnReinforce(
  (sender): RnnSenderReinforce(
    (agent): LayerWrapper(
      (output): Linear(in_features=2, out_features=128, bias=True)
    )
    (hidden_to_output): Linear(in_features=128, out_features=128, bias=True)
    (embedding): Embedding(128, 8)
    (cells): ModuleList(
      (0): RNNCell(8, 128)
    )
  )
  (receiver): RnnReceiverDeterministic(
    (agent): LayerWrapper(
      (output): Linear(in_features=128, out_features=1, bias=True)
    )
    (encoder): RnnEncoder(
      (cell): RNN(8, 128, batch_first=True)
      (embedding): Embedding(128, 8)
    )
  )
  (mechanics): CommunicationRnnReinforce()
)
Number of parameters 54409

----------
Start of training... 2021-11-11 19:43:46.333848
{"loss": 41.564273834228516, "acc": 0.057692307978868484, "sender_entropy": 2.3245608806610107, "receiver_entropy": 0.0, "length": 1.9807692766189575, "mode": "train", "epoc